# Import Statements

In [2]:
import os
import pickle
import warnings
warnings.filterwarnings('ignore')

import geodata
import xarray as xr

import numpy as np
import pandas as pd
import geopandas as gpd

from shapely.geometry import shape, Point, Polygon
from shapely.ops import cascaded_union
import statsmodels.api as sm

import geoplot
import seaborn as sns
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import plotly.express as px

# Load from pickle

In [3]:
os.chdir('../data/pickle')
# district data
file = open("districts.pickle",'rb')
districts = pickle.load(file)
file.close()
# ranked district data
file = open("JPCD_sum.pickle",'rb')
JPCD_sum = pickle.load(file)
file.close()
# state shapes
file = open("states.pickle",'rb')
states = pickle.load(file)
file.close()
# xarrays
file = open("xarray_ds_wind.pickle",'rb')
xarray_ds_wind = pickle.load(file)
file.close()
file = open("xarray_ds_solar.pickle",'rb')
xarray_ds_solar = pickle.load(file)
file.close()
# renewable energy targets
file = open("wind_t_30.pickle",'rb')
wind_t_30 = pickle.load(file)
file.close()
file = open("solar_t_30.pickle",'rb')
solar_t_30 = pickle.load(file)
file.close()
file = open("wind_t_50_base.pickle",'rb')
wind_t_50_base = pickle.load(file)
file.close()
file = open("wind_t_50_lc.pickle",'rb')
wind_t_50_lc = pickle.load(file)
file.close()
file = open("solar_t_50_base.pickle",'rb')
solar_t_50_base = pickle.load(file)
file.close()
file = open("solar_t_50_lc.pickle",'rb')
solar_t_50_lc = pickle.load(file)
file.close()
# legend
file = open("state_legend.pickle",'rb')
state_legend = pickle.load(file)
file.close()
# coal incumbency states and districts
file = open("high_districts.pickle",'rb')
high_districts = pickle.load(file)
file.close()
file = open("high_states.pickle",'rb')
high_states = pickle.load(file)
file.close()
file = open("mid_districts.pickle",'rb')
mid_districts = pickle.load(file)
file.close()
file = open("mid_states.pickle",'rb')
mid_states = pickle.load(file)
file.close()
file = open("low_districts.pickle",'rb')
low_districts = pickle.load(file)
file.close()
file = open("low_states.pickle",'rb')
low_states = pickle.load(file)
file.close()
file = open("all_districts.pickle",'rb')
all_districts = pickle.load(file)
file.close()
file = open("all_states.pickle",'rb')
all_states = pickle.load(file)
file.close()
#combined with cutout
file = open("solar_combine_high.pickle",'rb')
solar_combine_high = pickle.load(file)
file.close()
file = open("solar_combine_mid.pickle",'rb')
solar_combine_mid = pickle.load(file)
file.close()
file = open("solar_combine_low.pickle",'rb')
solar_combine_low = pickle.load(file)
file.close()
file = open("solar_combine_all.pickle",'rb')
solar_combine_all = pickle.load(file)
file.close()
file = open("wind_combine_high.pickle",'rb')
wind_combine_high = pickle.load(file)
file.close()
file = open("wind_combine_mid.pickle",'rb')
wind_combine_mid = pickle.load(file)
file.close()
file = open("wind_combine_low.pickle",'rb')
wind_combine_low = pickle.load(file)
file.close()
file = open("wind_combine_all.pickle",'rb')
wind_combine_all = pickle.load(file)
file.close()

# Create Cutout

In [3]:
## CUTOUT
cutout = geodata.Cutout(name = "india-2018-era5-wind-solar-hourly",
                        module = "era5",
                        weather_data_config = "wind_solar_hourly",
                        xs = slice(68, 98),
                        ys = slice(6, 37),
                        years=slice(2018, 2018),
                        months=slice(1,12))

cutout.prepare()

True

# Download India 2018 ERA5 Hourly Weather Data

In [ ]:
DS_hourly = geodata.Dataset(module="era5",
                            weather_data_config = "wind_solar_hourly",
                            bounds=[37, 68, 6, 98],
                            years=slice(2018, 2018),
                            months=slice(1,12))

if DS_hourly.prepared == False:
	DS_hourly.get_data()

# Get Wind & Solar Profiles

In [ ]:
ds_wind = geodata.convert.wind(cutout, 
                               turbine='Siemens_SWT_107_3600kW')

ds_solar = geodata.convert.pv(cutout,
                              panel = "KANEKA",
                              orientation = "latitude_optimal")

In [ ]:
ds_wind = ds_wind.reset_coords(['lon', 'lat'], drop = True).rename({'x': 'lon', 'y': 'lat'})
ds_solar = ds_solar.reset_coords(['lon', 'lat'], drop = True).rename({'x': 'lon', 'y': 'lat'})

ds_wind.sortby(['lon', 'lat'])
ds_solar.sortby(['lon', 'lat'])

xarray_ds_wind = ds_wind.to_dataset(name = 'wind')
xarray_ds_solar = ds_solar.to_dataset(name = 'solar')

xarray_ds_wind = xarray_ds_wind.coarsen(time = 8760, boundary = 'exact').mean()
xarray_ds_solar = xarray_ds_solar.coarsen(time = 8760, boundary = 'exact').mean()

## Rank Districts by "Coal Incumbency"

### Calculate cdfs

In [ ]:
jobs_cdf = sm.distributions.ECDF(districts['Coal Job %'].dropna())
pensions_cdf = sm.distributions.ECDF(districts['Coal Pensioners %'].dropna())
dmf_cdf = sm.distributions.ECDF(districts[districts['DMF USD'] > 0]['DMF USD'].dropna())
csr_cdf = sm.distributions.ECDF(districts[districts['CSR USD'] > 0]['CSR USD'].dropna())

In [ ]:
plt.step(jobs_cdf.x, jobs_cdf.y)
plt.show()
plt.step(pensions_cdf.x, pensions_cdf.y)
plt.show()
plt.step(dmf_cdf.x, dmf_cdf.y)
plt.show()
plt.step(csr_cdf.x, csr_cdf.y)
plt.show()

In [ ]:
def return_edges(cdf):
    bin_edges = []
    bin_edges.append(cdf.x[0])

    for lst in np.array_split(cdf.x, 3):
        bin_edges.append(lst[len(lst) - 1])
        
    return bin_edges

def return_groups(val, bin_edges):
    if val == 0:
        return 0
    elif val >= bin_edges[2] and val <= bin_edges[3]:
        return 3
    elif val >= bin_edges[1] and val <= bin_edges[2]:
        return 2
    elif val >= bin_edges[0] and val <= bin_edges[1]:
        return 1
    else:
        return None

In [ ]:
# Bins
jobs_edges = return_edges(jobs_cdf)
pensions_edges = return_edges(pensions_cdf)
dmf_edges = return_edges(csr_cdf)
csr_edges = return_edges(dmf_cdf)

# Assign labels to equal percentile groups 
job_groups = districts['Coal Job %'].apply(lambda x: return_groups(x, jobs_edges))
pension_groups = districts['Coal Pensioners %'].apply(lambda x: return_groups(x, pensions_edges))
csr_groups = districts['CSR USD'].apply(lambda x: return_groups(x, csr_edges))
dmf_groups = districts['DMF USD'].apply(lambda x: return_groups(x, dmf_edges))

# Create new columns 
JPCD_sum = districts.assign(
    J = job_groups, 
    P = pension_groups, 
    C = csr_groups,
    D = dmf_groups
)
JPCD_sum = JPCD_sum[['State Name', 'District Name', 'Geometry', 'J', 'P', 'C', 'D']]

# Prepare for weighted sum 
JPCD_sum['J'] = JPCD_sum['J'].apply(lambda x: x*1)
JPCD_sum['P'] = JPCD_sum['P'].apply(lambda x: x*1/2)
JPCD_sum['C'] = JPCD_sum['C'].apply(lambda x: x*1/3)
JPCD_sum['D'] = JPCD_sum['D'].apply(lambda x: x*1/4)

# Create Rank Score by summing
JPCD_sum['Score'] = JPCD_sum[['J', 'P', 'D', 'C']].sum(axis = 1)
scores_cdf = sm.distributions.ECDF(JPCD_sum[JPCD_sum['Score'] > 0]['Score'])
scores_edges = return_edges(scores_cdf)
JPCD_sum['Rank'] = JPCD_sum['Score'].apply(lambda x: return_groups(x, scores_edges))
JPCD_sum

In [ ]:
high = JPCD_sum[JPCD_sum['Rank'] == 3]
high_states = np.unique(high['State Name'])
high_districts = cascaded_union(high['Geometry'])

mid = JPCD_sum[JPCD_sum['Rank'].isin([2,1])]
mid_states = np.unique(mid['State Name'])
mid_districts = cascaded_union(mid['Geometry'])

low = JPCD_sum[JPCD_sum['Rank'] == 0]
low_states = np.unique(low['State Name'])
low_districts = cascaded_union(low['Geometry'])

allc = JPCD_sum[JPCD_sum['Rank'].isin([0,1,2,3])]
all_states = np.unique(allc['State Name'])
all_districts = cascaded_union(allc['Geometry'])

In [ ]:
os.chdir('../pickle')
# export to pickle
filehandler = open("JPCD_sum.pickle","wb")
pickle.dump(JPCD_sum, filehandler)
filehandler.close()
filehandler = open("high_districts.pickle","wb")
pickle.dump(high_districts, filehandler)
filehandler.close()
filehandler = open("high_states.pickle","wb")
pickle.dump(high_states, filehandler)
filehandler.close()
filehandler = open("mid_districts.pickle","wb")
pickle.dump(mid_districts, filehandler)
filehandler.close()
filehandler = open("mid_states.pickle","wb")
pickle.dump(mid_states, filehandler)
filehandler.close()
filehandler = open("low_districts.pickle","wb")
pickle.dump(low_districts, filehandler)
filehandler.close()
filehandler = open("low_states.pickle","wb")
pickle.dump(low_states, filehandler)
filehandler.close()
filehandler = open("all_districts.pickle","wb")
pickle.dump(all_districts, filehandler)
filehandler.close()
filehandler = open("all_states.pickle","wb")
pickle.dump(all_states, filehandler)
filehandler.close()

# Transmission / Substation Data

In [ ]:
transmission = gpd.read_file('cae13821b4b7807f792aa0c03e0fd75903dae11dbd363484b1376ab9.shp')
transmission = transmission.drop(columns=['name']).reset_index()
transmission = gpd.GeoDataFrame(transmission, geometry='geometry')
transmission.to_file("transmission.shp", driver='ESRI Shapefile')

In [ ]:
substations = transmission.geometry.apply(lambda x: Point(x.bounds[:2], x.bounds[2:])).explode().reset_index()
substations = substations.drop(columns=['level_1'])
substations.columns = ['index', 'geometry']
substations = gpd.GeoDataFrame(substations, geometry='geometry')
substations.to_file("substations.shp", driver='ESRI Shapefile')

In [ ]:
grid_cells = pd.DataFrame(cutout.grid_cells()).reset_index()
grid_cells.columns = ['index', 'geometry']
grid_cells = gpd.GeoDataFrame(grid_cells, geometry='geometry')
grid_cells.to_file("grid_cells.shp", driver='ESRI Shapefile')

# LCOE Calculation

### Calculate Distances using QGIS
- https://www.qgistutorials.com/en/docs/3/nearest_neighbor_analysis.html

In [ ]:
transmission = pd.read_csv('transmission_distances.csv')
transmission = pd.DataFrame(cutout.grid_coordinates()).join(transmission).drop(columns=['index', 'HubName'])
transmission.columns = ['lon', 'lat', 'Closest Transmission Line Distance (km)']
transmission = transmission.set_index(['lon', 'lat'])
transmission

In [ ]:
os.chdir('../data/tables')
substation = pd.read_csv('substation_distance.csv')
substation = pd.DataFrame(cutout.grid_coordinates()).join(substation).drop(columns=['index', 'HubName'])
substation.columns = ['lon', 'lat', 'Closest Substation Distance (km)']
substation = substation.set_index(['lon', 'lat'])
substation

In [ ]:
df_ds_solar = xarray_ds_solar.to_dataframe().reset_index().set_index(['lon', 'lat'])
df_ds_solar['substation_distance'] = substation['Closest Substation Distance (km)']
df_ds_solar = df_ds_solar[df_ds_solar['solar'] >= 0.1]
#IRENA 2020
df_ds_solar['LCOE ($/MWh) low'] = (0.075 * (850 + df_ds_solar['substation_distance'] * 0.45) + 10) * 1000 / (
    df_ds_solar['solar'] * 8760)
#IRENA 2020
df_ds_solar['LCOE ($/MWh) mid'] = (0.10 * (850 + df_ds_solar['substation_distance'] * 0.45) + 10) * 1000 / (
    df_ds_solar['solar'] * 8760)
# Steffen
df_ds_solar['LCOE ($/MWh) high'] = (0.125 * (850 + df_ds_solar['substation_distance'] * 0.45) + 10) * 1000 / (
    df_ds_solar['solar'] * 8760)
xarray_ds_solar = df_ds_solar.reset_index().set_index(['time', 'lat', 'lon']).to_xarray()

df_ds_wind = xarray_ds_wind.to_dataframe().reset_index().set_index(['lon', 'lat'])
df_ds_wind['substation_distance'] = substation['Closest Substation Distance (km)']
df_ds_wind = df_ds_wind[df_ds_wind['wind'] >= 0.04]
# Steffen
df_ds_wind['LCOE ($/MWh) low'] = (0.075 * (1250 + df_ds_wind['substation_distance'] * 0.45) + 15) * 1000 / (
    df_ds_wind['wind'] * 8760)
# Steffen
df_ds_wind['LCOE ($/MWh) mid'] = (0.10 * (1250 + df_ds_wind['substation_distance'] * 0.45) + 15) * 1000 / (
    df_ds_wind['wind'] * 8760)
# Steffen
df_ds_wind['LCOE ($/MWh) high'] = (0.125 * (1250 + df_ds_wind['substation_distance'] * 0.45) + 15) * 1000 / (
    df_ds_wind['wind'] * 8760)
xarray_ds_wind = df_ds_wind.reset_index().set_index(['time', 'lat', 'lon']).to_xarray()

In [ ]:
os.chdir('../pickle')
# export to pickle
filehandler = open("xarray_ds_solar.pickle","wb")
pickle.dump(xarray_ds_solar, filehandler)
filehandler.close()
filehandler = open("xarray_ds_wind.pickle","wb")
pickle.dump(xarray_ds_wind, filehandler)
filehandler.close()

# Load MODIS Mask

In [ ]:
os.chdir('../masks')
india_solar_high = geodata.mask.load_mask("India Solar High")
india_solar_mid = geodata.mask.load_mask("India Solar Mid")
india_solar_low = geodata.mask.load_mask("India Solar Low")
india_solar_all = geodata.mask.load_mask("India Solar All")

india_wind_high = geodata.mask.load_mask("India Wind High")
india_wind_mid = geodata.mask.load_mask("India Wind Mid")
india_wind_low = geodata.mask.load_mask("India Wind Low")
india_wind_all = geodata.mask.load_mask("India Wind All")

In [ ]:
os.chdir('../masks')
india_solar_high = geodata.Mask("India Solar High", layer_path = {
    'suitability': 'MODIS_INDIA_SOLAR.tif'
})
india_solar_mid = geodata.Mask("India Solar Mid", layer_path = {
    'suitability': 'MODIS_INDIA_SOLAR.tif'
})
india_solar_low = geodata.Mask("India Solar Low", layer_path = {
    'suitability': 'MODIS_INDIA_SOLAR.tif'
})
india_solar_all = geodata.Mask("India Solar All", layer_path = {
    'suitability': 'MODIS_INDIA_SOLAR.tif'
})

india_wind_high = geodata.Mask("India Wind High", layer_path = {
    'suitability': 'MODIS_INDIA_WIND.tif'
})
india_wind_mid = geodata.Mask("India Wind Mid", layer_path = {
    'suitability': 'MODIS_INDIA_WIND.tif'
})
india_wind_low = geodata.Mask("India Wind Low", layer_path = {
    'suitability': 'MODIS_INDIA_WIND.tif'
})
india_wind_all = geodata.Mask("India Wind All", layer_path = {
    'suitability': 'MODIS_INDIA_WIND.tif'
})

# Extract District Shapes as Mask Layers

In [ ]:
high_districts = {'districts': high_districts}
mid_districts = {'districts': mid_districts}
low_districts = {'districts': low_districts}
all_districts = {'districts': all_districts}

In [ ]:
india_solar_high.extract_shapes(high_districts, layer = 'suitability')
india_solar_mid.extract_shapes(mid_districts, layer = 'suitability')
india_solar_low.extract_shapes(low_districts, layer = 'suitability')
india_solar_all.extract_shapes(all_districts, layer = 'suitability')

india_wind_high.extract_shapes(high_districts, layer = 'suitability')
india_wind_mid.extract_shapes(mid_districts, layer = 'suitability')
india_wind_low.extract_shapes(low_districts, layer = 'suitability')
india_wind_all.extract_shapes(all_districts, layer = 'suitability')

In [ ]:
india_solar_high.add_shape_layer({
    'districts': high_districts['districts'],
}, reference_layer='suitability', exclude=True)

india_solar_mid.add_shape_layer({
    'districts': mid_districts['districts'],
}, reference_layer='suitability', exclude=True)

india_solar_low.add_shape_layer({
    'districts': low_districts['districts'],
}, reference_layer='suitability', exclude=True)

india_solar_all.add_shape_layer({
    'districts': all_districts['districts'],
}, reference_layer='suitability', exclude=True)

india_wind_high.add_shape_layer({
    'districts': high_districts['districts']
}, reference_layer='suitability', exclude=True)

india_wind_mid.add_shape_layer({
    'districts': mid_districts['districts'],
}, reference_layer='suitability', exclude=True)

india_wind_low.add_shape_layer({
    'districts': low_districts['districts'],
}, reference_layer='suitability', exclude=True)

india_wind_all.add_shape_layer({
    'districts': all_districts['districts'],
}, reference_layer='suitability', exclude=True)

# Merge Districts + Suitability

In [ ]:
india_solar_high.merge_layer(layers = ['suitability', 'districts'], show_raster=False)
india_solar_mid.merge_layer(layers = ['suitability', 'districts'], show_raster=False)
india_solar_low.merge_layer(layers = ['suitability', 'districts'], show_raster=False)
india_solar_all.merge_layer(layers = ['suitability', 'districts'], show_raster=False)

india_wind_high.merge_layer(layers = ['suitability', 'districts'], show_raster=False)
india_wind_mid.merge_layer(layers = ['suitability', 'districts'], show_raster=False)
india_wind_low.merge_layer(layers = ['suitability', 'districts'], show_raster=False)
india_wind_all.merge_layer(layers = ['suitability', 'districts'], show_raster=False)

## Extract Shapes

In [ ]:
india_solar_high.extract_shapes({x: states[x] for x in high_states if x in states.keys()})
india_solar_mid.extract_shapes({x: states[x] for x in mid_states if x in states.keys()})
india_solar_low.extract_shapes({x: states[x] for x in low_states if x in states.keys()})
india_solar_all.extract_shapes({x: states[x] for x in all_states if x in states.keys()})

india_wind_high.extract_shapes({x: states[x] for x in high_states if x in states.keys()})
india_wind_mid.extract_shapes({x: states[x] for x in mid_states if x in states.keys()})
india_wind_low.extract_shapes({x: states[x] for x in low_states if x in states.keys()})
india_wind_all.extract_shapes({x: states[x] for x in all_states if x in states.keys()})

# Combine Mask with Cutout

In [ ]:
india_solar_high.save_mask()
india_solar_mid.save_mask()
india_solar_low.save_mask()
india_solar_all.save_mask()

india_wind_high.save_mask()
india_wind_mid.save_mask()
india_wind_low.save_mask()
india_wind_all.save_mask()

In [ ]:
cutout.add_mask("India Solar High", merged_mask=False)
cutout.add_grid_area()
solar_combine_high = cutout.mask(dataset = xarray_ds_solar)

cutout.add_mask("India Solar Mid", merged_mask=False)
cutout.add_grid_area()
solar_combine_mid = cutout.mask(dataset = xarray_ds_solar)

cutout.add_mask("India Solar Low", merged_mask=False)
cutout.add_grid_area()
solar_combine_low = cutout.mask(dataset = xarray_ds_solar)

cutout.add_mask("India Solar All", merged_mask=False)
cutout.add_grid_area()
solar_combine_all = cutout.mask(dataset = xarray_ds_solar)

cutout.add_mask("India Wind High", merged_mask=False)
cutout.add_grid_area()
wind_combine_high = cutout.mask(dataset = xarray_ds_wind)

cutout.add_mask("India Wind Mid", merged_mask=False)
cutout.add_grid_area()
wind_combine_mid = cutout.mask(dataset = xarray_ds_wind)

cutout.add_mask("India Wind Low", merged_mask=False)
cutout.add_grid_area()
wind_combine_low = cutout.mask(dataset = xarray_ds_wind)

cutout.add_mask("India Wind All", merged_mask=False)
cutout.add_grid_area()
wind_combine_all = cutout.mask(dataset = xarray_ds_wind)

In [ ]:
os.chdir('../pickle')
# export to pickle
filehandler = open("solar_combine_high.pickle","wb")
pickle.dump(solar_combine_high, filehandler)
filehandler.close()
filehandler = open("solar_combine_mid.pickle","wb")
pickle.dump(solar_combine_mid, filehandler)
filehandler.close()
filehandler = open("solar_combine_low.pickle","wb")
pickle.dump(solar_combine_low, filehandler)
filehandler.close()
filehandler = open("solar_combine_all.pickle","wb")
pickle.dump(solar_combine_all, filehandler)
filehandler.close()
filehandler = open("wind_combine_high.pickle","wb")
pickle.dump(wind_combine_high, filehandler)
filehandler.close()
filehandler = open("wind_combine_mid.pickle","wb")
pickle.dump(wind_combine_mid, filehandler)
filehandler.close()
filehandler = open("wind_combine_low.pickle","wb")
pickle.dump(wind_combine_low, filehandler)
filehandler.close()
filehandler = open("wind_combine_all.pickle","wb")
pickle.dump(wind_combine_all, filehandler)
filehandler.close()

# State Renewable Targets

## 2030

In [ ]:
multiple = 140/sum(wind_t_30.values())
wind_t_30 = {k: wind_t_30[k] * multiple for k in wind_t_30.keys()}

In [4]:
sum(wind_t_30.values())

140.0

In [ ]:
multiple = 280/sum(solar_t_30.values())
solar_t_30 = {k: solar_t_30[k] * multiple for k in solar_t_30.keys()}

In [5]:
sum(solar_t_30.values())

280.0000000000001

In [ ]:
sum(solar_t_30.values()) + sum(wind_t_30.values())

## 2050

In [ ]:
base_multiple = 445/sum(wind_t_30.values())
lc_multiple = 557/sum(wind_t_30.values())

wind_t_50_base = {k: wind_t_30[k] * base_multiple for k in wind_t_30.keys()}
wind_t_50_lc = {k: wind_t_30[k] * lc_multiple for k in wind_t_30.keys()}

In [ ]:
base_multiple = 575/sum(solar_t_30.values())
lc_multiple = 1689/sum(solar_t_30.values())

solar_t_50_base = {k: solar_t_30[k] * base_multiple for k in solar_t_30.keys()}
solar_t_50_lc = {k: solar_t_30[k] * lc_multiple for k in solar_t_30.keys()}

In [8]:
sum(solar_t_50_base.values())

575.0

In [9]:
sum(wind_t_50_base.values())

445.0

In [10]:
sum(solar_t_50_lc.values())

1689.0

In [11]:
sum(wind_t_50_lc.values())

557.0000000000001

In [12]:
sum(solar_t_50_base.values()) + sum(wind_t_50_base.values())

1020.0

In [13]:
sum(solar_t_50_lc.values()) + sum(wind_t_50_lc.values())

2246.0

In [ ]:
# export to pickle
os.chdir('../pickle')
filehandler = open("wind_t_30.pickle","wb")
pickle.dump(wind_t_30, filehandler)
filehandler.close()
filehandler = open("wind_t_50_base.pickle","wb")
pickle.dump(wind_t_50_base, filehandler)
filehandler.close()
filehandler = open("wind_t_50_lc.pickle","wb")
pickle.dump(wind_t_50_lc, filehandler)
filehandler.close()

filehandler = open("solar_t_30.pickle","wb")
pickle.dump(solar_t_30, filehandler)
filehandler.close()
filehandler = open("solar_t_50_base.pickle","wb")
pickle.dump(solar_t_50_base, filehandler)
filehandler.close()
filehandler = open("solar_t_50_lc.pickle","wb")
pickle.dump(solar_t_50_lc, filehandler)
filehandler.close()

# Plot CF Supply Curves

In [ ]:
state_colors = list(
    set(px.colors.qualitative.Plotly).union(
        set(px.colors.qualitative.Vivid)
    )
) * 2
state_legend = {list(states.keys())[i]: state_colors[i] for i in range(len(states))}

In [ ]:
os.chdir('../pickle')
# export to pickle
filehandler = open("state_legend.pickle","wb")
pickle.dump(state_legend, filehandler)
filehandler.close()

In [4]:
def make_figures(df, col, wacc=None):
    df = df[df[col] > 0]
    if col == 'wind':
        # deshmukh
        df['cap low'] = df['area'] * df['mask'] * 2.25 / 1000
        # Lu / NREL / Prof
        df['cap mid'] = df['area'] * df['mask'] * 3.9 / 1000
        # deshmukh
        df['cap high'] = df['area'] * df['mask'] * 9 / 1000
    else:
        # deshmukh
        df['cap low'] = df['area'] * df['mask'] * 7.5 / 1000
        # Lu / NREL / Prof
        df['cap mid'] = df['area'] * df['mask'] * 27.7 / 1000
        # deshmukh
        df['cap high'] = df['area'] * df['mask'] * 30 / 1000
    if wacc != None:
        df = df.sort_values(by = 'LCOE ($/MWh) {}'.format(wacc), ascending = True)
    else:
        df = df.sort_values(by = col, ascending = False)
    df = df[df['cap low'] > 0]
    df = df[df['cap mid'] > 0]
    df = df[df['cap high'] > 0]
    df['cumsum low'] = df['cap low'].cumsum()
    df['cumsum mid'] = df['cap mid'].cumsum()
    df['cumsum high'] = df['cap high'].cumsum()
    return df.reset_index(drop=True)

def batch_figures(xr_provs, t_30, t_50_base, t_50_lc, legend, col='solar', coal='all', wacc=None):
    dfs = {xr_prov:[] for xr_prov in xr_provs}
    for xr_prov in xr_provs:
        df = xr_provs[xr_prov].to_dataframe().reset_index(drop=False)
        df = make_figures(df, col, wacc)
        dfs[xr_prov] = df
    fig = go.Figure()
    for xr_prov in xr_provs:
        if xr_prov not in ['districts', 'Eastern', 'North-Eastern', 'Northern', 'Southern', 'Western']:
            if wacc != None:
                fig.add_trace(
                    go.Scatter(
                        x=dfs[xr_prov]['cumsum mid'],
                        y=dfs[xr_prov]['LCOE ($/MWh) {}'.format(wacc)],
                        mode='lines', 
                        line=go.scatter.Line(color=legend[xr_prov]),
                        name=xr_prov,
                        showlegend=True
                    )
                )
                fig.update_layout(
                    xaxis_title="Cumulative Capacity (GW)",
                    yaxis_title="LCOE ($/MWh)",
                    legend_title="State",
                )
            else:
                fig.add_trace(
                    go.Scatter(
                        x=dfs[xr_prov]['cumsum mid'],
                        y=dfs[xr_prov][col],
                        mode='lines', 
                        line=go.scatter.Line(color=legend[xr_prov]),
                        name=xr_prov,
                        showlegend=True
                    )
                )
                fig.update_layout(
                    xaxis_title="Cumulative Capacity (GW)",
                    yaxis_title="Capacity Factor (%)",
                    legend_title="State",
                )
    fig.add_vline(
        x=sum(t_30.values()),
        annotation_text="2030: {} GW".format(round(sum(t_30.values()), 2)),
        annotation_position='bottom right',
        line_dash="dash"
    )
    fig.add_vline(
        x=sum(t_50_base.values()),
        annotation_text="2050 BAU: {} GW".format(round(sum(t_50_base.values()), 2)),
        annotation_position='right',
        line_dash="dash"
    )
    fig.add_vline(
        x=sum(t_50_lc.values()),
        annotation_text="2050 LC: {} GW".format(round(sum(t_50_lc.values()), 2)),
        annotation_position='bottom right',
        line_dash="dash"
    )
    fig.show()
    if wacc != None:
        fig.write_image("{}_{}_lcoe_supplies.png".format(col, coal))
    else:
        fig.write_image("{}_{}_cf_supplies.png".format(col, coal))
    return dfs

# State Figures

In [5]:
os.chdir('../../outputs/plots')

In [6]:
### Solar CF

solar_high_coal = batch_figures(solar_combine_high, solar_t_30, solar_t_50_base, solar_t_50_lc, state_legend, 
                                     col='solar', coal='high')

solar_mid_coal = batch_figures(solar_combine_mid, solar_t_30, solar_t_50_base, solar_t_50_lc, state_legend, 
                                      col='solar', coal='medium')

solar_low_coal = batch_figures(solar_combine_low, solar_t_30, solar_t_50_base, solar_t_50_lc, state_legend,
                                      col='solar', coal='low')

solar_all_coal = batch_figures(solar_combine_all, solar_t_30, solar_t_50_base, solar_t_50_lc, state_legend, 
                                      col='solar', coal='all')

### Solar LCOE
solar_high_coal_lcoe = batch_figures(solar_combine_high, solar_t_30, solar_t_50_base, solar_t_50_lc, state_legend, 
                                         col='solar', coal='high', wacc='mid')

solar_mid_coal_lcoe = batch_figures(solar_combine_mid, solar_t_30, solar_t_50_base, solar_t_50_lc, state_legend, 
                                         col='solar', coal='medium', wacc='mid')

solar_low_coal_lcoe = batch_figures(solar_combine_low, solar_t_30, solar_t_50_base, solar_t_50_lc, state_legend, 
                                         col='solar', coal='low', wacc='mid')

solar_all_coal_lcoe = batch_figures(solar_combine_all, solar_t_30, solar_t_50_base, solar_t_50_lc, state_legend, 
                                         col='solar', coal='all', wacc='mid')

### Wind CF
wind_high_coal = batch_figures(wind_combine_high, wind_t_30, wind_t_50_base, wind_t_50_lc, state_legend, 
                                       col='wind', coal='high')

wind_mid_coal = batch_figures(wind_combine_mid, wind_t_30, wind_t_50_base, wind_t_50_lc, state_legend,
                                      col='wind', coal='medium')

wind_low_coal = batch_figures(wind_combine_low, wind_t_30, wind_t_50_base, wind_t_50_lc, state_legend,
                                      col='wind', coal='low')

wind_all_coal = batch_figures(wind_combine_all, wind_t_30, wind_t_50_base, wind_t_50_lc, state_legend,
                                      col='wind', coal='all')

### Wind LCOE
wind_high_coal_lcoe = batch_figures(wind_combine_high, wind_t_30, wind_t_50_base, wind_t_50_lc, state_legend,
                                        col='wind', coal='high', wacc='mid')

wind_mid_coal_lcoe = batch_figures(wind_combine_mid, wind_t_30, wind_t_50_base, wind_t_50_lc, state_legend,
                                       col='wind', coal='medium', wacc='mid')

wind_low_coal_lcoe = batch_figures(wind_combine_low, wind_t_30, wind_t_50_base, wind_t_50_lc, state_legend,
                                       col='wind', coal='low', wacc='mid')

wind_all_coal_lcoe = batch_figures(wind_combine_all, wind_t_30, wind_t_50_base, wind_t_50_lc, state_legend,
                                       col='wind', coal='all', wacc='mid')

# Calculate Averages & Plot Figures by State

In [7]:
def plot_fig_state(dfs, state, t_30, t_50_base, t_50_lc, col='solar', coal='all', pf='mid', wacc=None, show=False):
    df = dfs.get(state)                          
    avg_30 = np.nan
    avg_50_base = np.nan
    avg_50_lc = np.nan
    df_30 = np.nan
    df_50_base = np.nan
    df_50_lc = np.nan
    
    if df is not None:
        if len(df) > 0:
            if df['cumsum {}'.format(pf)].values[0] > t_30[state]:
                df_30 = df.head(1)
            else:
                if (df['cumsum {}'.format(pf)].values[-1] > t_30[state]):
                    df_30 = df[df['cumsum {}'.format(pf)] <= t_30[state]]                
            if df['cumsum {}'.format(pf)].values[0] > t_50_base[state]:
                df_50_base = df.head(1)
            else:
                if (df['cumsum {}'.format(pf)].values[-1] > t_50_base[state]):
                    df_50_base = df[df['cumsum {}'.format(pf)] <= t_50_base[state]]
            if df['cumsum {}'.format(pf)].values[0] > t_50_lc[state]:
                df_50_lc = df.head(1)
            else:
                if (df['cumsum {}'.format(pf)].values[-1] > t_50_lc[state]):
                    df_50_lc = df[df['cumsum {}'.format(pf)] <= t_50_lc[state]]                
        else:
            return avg_30, avg_50_base, avg_50_lc, df_30, df_50_base, df_50_lc
    else:
        return avg_30, avg_50_base, avg_50_lc, df_30, df_50_base, df_50_lc 
    
    if wacc != None: 
        if df_30 is not np.nan:
            avg_30 = round(sum(df_30['cap {}'.format(pf)] * df_30['LCOE ($/MWh) {}'.format(wacc)]) / sum(df_30['cap {}'.format(pf)]), 2)        
        if df_50_base is not np.nan:
            avg_50_base = round(sum(df_50_base['cap {}'.format(pf)] * df_50_base['LCOE ($/MWh) {}'.format(wacc)]) / sum(df_50_base['cap {}'.format(pf)]), 2)
        if df_50_lc is not np.nan:
            avg_50_lc = round(sum(df_50_lc['cap {}'.format(pf)] * df_50_lc['LCOE ($/MWh) {}'.format(wacc)]) / sum(df_50_lc['cap {}'.format(pf)]), 2)
    else:
        if df_30 is not np.nan:
            avg_30 = round(sum(df_30['cap {}'.format(pf)] * df_30[col]) / sum(df_30['cap {}'.format(pf)]), 2)        
        if df_50_base is not np.nan:
            avg_50_base = round(sum(df_50_base['cap {}'.format(pf)] * df_50_base[col]) / sum(df_50_base['cap {}'.format(pf)]), 2)
        if df_50_lc is not np.nan:
            avg_50_lc = round(sum(df_50_lc['cap {}'.format(pf)] * df_50_lc[col]) / sum(df_50_lc['cap {}'.format(pf)]), 2)

    if show:
        fig = go.Figure() 
        if t_30[state] > 0:
            fig.add_vline(
                x=t_30[state],
                annotation_text="2030: {} GW".format(round(t_30[state], 2)),
                annotation_position='bottom right',
                line_dash="dash"
            )
            fig.add_vline(
                x=t_50_base[state],
                annotation_text="2050 BAU: {} GW".format(round(t_50_base[state], 2)),
                annotation_position='bottom right',
                line_dash="dash"
            )
            fig.add_vline(
                x=t_50_lc[state],
                annotation_text="2050 LC: {} GW".format(round(t_50_lc[state], 2)),
                annotation_position='bottom right',
                line_dash="dash"
            )
            if len(dfs[state]['cumsum {}'.format(pf)]) > 0:
                fig.update_xaxes(
                    range=(dfs[state]['cumsum {}'.format(pf)][0], 55)
                )
        if lcoe:
            fig.add_trace(
                go.Scatter(
                    x=dfs[state]['cumsum {}'.format(pf)],
                    y=dfs[state]['LCOE ($/MWh) {}'.format(wacc)],
                )
            )
            fig.add_hline(
                y=avg_30,
                annotation_text="Mean LCOE 2030: {} $/MWh".format(avg_30),
                annotation_position='bottom left',
                line_dash="dash"
            )
            fig.add_hline(
                y=avg_50_base,
                annotation_text="Mean LCOE 2050 BAU: {} $/MWh".format(avg_50_base),
                annotation_position='top left',
                line_dash="dash"
            )
            fig.add_hline(
                y=avg_50_lc,
                annotation_text="Mean LCOE 2050 LC: {} $/MWh".format(avg_50_lc),
                annotation_position='top left',
                line_dash="dash"
            )
            fig.update_layout(
                xaxis_title="Cumulative Capacity (GW)",
                yaxis_title="LCOE ($/MWh)",
                legend_title="State",
            )
            if col == 'wind':
                fig.update_yaxes(
                    range=(40, 80)
                )
            fig.write_image("{}_{}_lcoe_supplies.png".format(state, col))
        else:
            fig.add_trace(
                go.Scatter(
                    x=dfs[state]['cumsum {}'.format(pf)],
                    y=dfs[state][col], 
                )
            )
            fig.add_hline(
                y=avg_30,
                annotation_text="Mean CF 2030: {}".format(avg_30),
                annotation_position='top left',
                line_dash="dash"
            )
            fig.add_hline(
                y=avg_50_base,
                annotation_text="Mean CF 2050 BAU: {}".format(avg_50_base),
                annotation_position='bottom left',
                line_dash="dash"
            )
            fig.add_hline(
                y=avg_50_lc,
                annotation_text="Mean CF 2050 LC: {}".format(avg_50_lc),
                annotation_position='bottom left',
                line_dash="dash"
            )
            fig.update_layout(
                xaxis_title="Cumulative Capacity (GW)",
                yaxis_title="Capacity Factor (%)",
                legend_title="State",
            )
            fig.write_image("{}_{}_cf_supplies.png".format(state, col))
        fig.show()
    return avg_30, avg_50_base, avg_50_lc, df_30, df_50_base, df_50_lc

# Get State Averages

In [8]:
keys = ['wind_2030', 'solar_2030', 'wind_2050_base', 'solar_2050_base', 'wind_2050_lc', 'solar_2050_lc']
high_capacities = {key: {state: 0 for state in states} for key in keys}
all_capacities = {key: {state: 0 for state in states} for key in keys}

In [9]:
averages_wind_2030 = {state: [] for state in states if wind_t_30[state] > 0}
averages_solar_2030 = {state: [] for state in states if solar_t_30[state] > 0}
averages_wind_2050_base = {state: [] for state in states if wind_t_50_base[state] > 0}
averages_solar_2050_base = {state: [] for state in states if solar_t_50_base[state] > 0}
averages_wind_2050_lc = {state: [] for state in states if wind_t_50_lc[state] > 0}
averages_solar_2050_lc = {state: [] for state in states if solar_t_50_lc[state] > 0}

for state in states:
    solar_high_coal_high_pf_avg_CF = plot_fig_state(solar_high_coal, state, solar_t_30, solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='high', pf='high')
    solar_high_coal_mid_pf_avg_CF = plot_fig_state(solar_high_coal, state, solar_t_30, solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='high', pf='mid')
    solar_high_coal_low_pf_avg_CF = plot_fig_state(solar_high_coal, state, solar_t_30, solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='high', pf='low')
    solar_high_coal_high_pf_high_wacc_avg_LCOE = plot_fig_state(solar_high_coal_lcoe, state, solar_t_30, 
                                                                solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='high', pf='high', wacc='high')
    solar_high_coal_high_pf_mid_wacc_avg_LCOE = plot_fig_state(solar_high_coal_lcoe, state, solar_t_30, 
                                                               solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='high', pf='high', wacc='mid')
    solar_high_coal_high_pf_low_wacc_avg_LCOE = plot_fig_state(solar_high_coal_lcoe, state, solar_t_30, 
                                                               solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='high', pf='high', wacc='low')
    solar_high_coal_mid_pf_high_wacc_avg_LCOE = plot_fig_state(solar_high_coal_lcoe, state, solar_t_30, 
                                                               solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='high', pf='mid', wacc='high')
    solar_high_coal_mid_pf_mid_wacc_avg_LCOE = plot_fig_state(solar_high_coal_lcoe, state, solar_t_30, 
                                                              solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='high', pf='mid', wacc='mid')
    solar_high_coal_mid_pf_low_wacc_avg_LCOE = plot_fig_state(solar_high_coal_lcoe, state, solar_t_30, 
                                                              solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='high', pf='mid', wacc='low')
    solar_high_coal_low_pf_high_wacc_avg_LCOE = plot_fig_state(solar_high_coal_lcoe, state, solar_t_30, 
                                                               solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='high', pf='low', wacc='high')
    solar_high_coal_low_pf_mid_wacc_avg_LCOE = plot_fig_state(solar_high_coal_lcoe, state, solar_t_30, 
                                                              solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='high', pf='low', wacc='mid')
    solar_high_coal_low_pf_low_wacc_avg_LCOE = plot_fig_state(solar_high_coal_lcoe, state, solar_t_30, 
                                                              solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='high', pf='low', wacc='low')
    wind_high_coal_high_pf_avg_CF = plot_fig_state(wind_high_coal, state, wind_t_30, wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='high', pf='high')
    wind_high_coal_mid_pf_avg_CF = plot_fig_state(wind_high_coal, state, wind_t_30, wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='high', pf='mid')
    wind_high_coal_low_pf_avg_CF = plot_fig_state(wind_high_coal, state, wind_t_30, wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='high', pf='low')
    wind_high_coal_high_pf_high_wacc_avg_LCOE = plot_fig_state(wind_high_coal_lcoe, state, wind_t_30, 
                                                               wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='high', pf='high', wacc='high')
    wind_high_coal_high_pf_mid_wacc_avg_LCOE = plot_fig_state(wind_high_coal_lcoe, state, wind_t_30, 
                                                              wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='high', pf='high', wacc='mid')
    wind_high_coal_high_pf_low_wacc_avg_LCOE = plot_fig_state(wind_high_coal_lcoe, state, wind_t_30, 
                                                              wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='high', pf='high', wacc='low')
    wind_high_coal_mid_pf_high_wacc_avg_LCOE = plot_fig_state(wind_high_coal_lcoe, state, wind_t_30, 
                                                              wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='high', pf='mid', wacc='high')
    wind_high_coal_mid_pf_mid_wacc_avg_LCOE = plot_fig_state(wind_high_coal_lcoe, state, wind_t_30, 
                                                             wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='high', pf='mid', wacc='mid')
    wind_high_coal_mid_pf_low_wacc_avg_LCOE = plot_fig_state(wind_high_coal_lcoe, state, wind_t_30, 
                                                             wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='high', pf='mid', wacc='low')
    wind_high_coal_low_pf_high_wacc_avg_LCOE = plot_fig_state(wind_high_coal_lcoe, state, wind_t_30, 
                                                              wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='high', pf='low', wacc='high')
    wind_high_coal_low_pf_mid_wacc_avg_LCOE = plot_fig_state(wind_high_coal_lcoe, state, wind_t_30, 
                                                             wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='high', pf='low', wacc='mid')
    wind_high_coal_low_pf_low_wacc_avg_LCOE = plot_fig_state(wind_high_coal_lcoe, state, wind_t_30, 
                                                             wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='high', pf='low', wacc='low')        

    solar_mid_coal_high_pf_avg_CF = plot_fig_state(solar_mid_coal, state, solar_t_30, solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='medium', pf='high')
    solar_mid_coal_mid_pf_avg_CF = plot_fig_state(solar_mid_coal, state, solar_t_30, solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='medium', pf='mid')
    solar_mid_coal_low_pf_avg_CF = plot_fig_state(solar_mid_coal, state, solar_t_30, solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='medium', pf='low')
    solar_mid_coal_high_pf_high_wacc_avg_LCOE = plot_fig_state(solar_mid_coal_lcoe, state, solar_t_30, 
                                                               solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='medium', pf='high', wacc='high')
    solar_mid_coal_high_pf_mid_wacc_avg_LCOE = plot_fig_state(solar_mid_coal_lcoe, state, solar_t_30, 
                                                              solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='medium', pf='high', wacc='mid')
    solar_mid_coal_high_pf_low_wacc_avg_LCOE = plot_fig_state(solar_mid_coal_lcoe, state, solar_t_30, 
                                                              solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='medium', pf='high', wacc='low')
    solar_mid_coal_mid_pf_high_wacc_avg_LCOE = plot_fig_state(solar_mid_coal_lcoe, state, solar_t_30, 
                                                              solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='medium', pf='mid', wacc='high')
    solar_mid_coal_mid_pf_mid_wacc_avg_LCOE = plot_fig_state(solar_mid_coal_lcoe, state, solar_t_30, 
                                                             solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='medium', pf='mid', wacc='mid')
    solar_mid_coal_mid_pf_low_wacc_avg_LCOE = plot_fig_state(solar_mid_coal_lcoe, state, solar_t_30, 
                                                             solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='medium', pf='mid', wacc='low')
    solar_mid_coal_low_pf_high_wacc_avg_LCOE = plot_fig_state(solar_mid_coal_lcoe, state, solar_t_30, 
                                                              solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='medium', pf='low', wacc='high')
    solar_mid_coal_low_pf_mid_wacc_avg_LCOE = plot_fig_state(solar_mid_coal_lcoe, state, solar_t_30, 
                                                             solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='medium', pf='low', wacc='mid')
    solar_mid_coal_low_pf_low_wacc_avg_LCOE = plot_fig_state(solar_mid_coal_lcoe, state, solar_t_30, 
                                                             solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='medium', pf='low', wacc='low')
    wind_mid_coal_high_pf_avg_CF = plot_fig_state(wind_mid_coal, state, wind_t_30, wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='medium', pf='high')
    wind_mid_coal_mid_pf_avg_CF = plot_fig_state(wind_mid_coal, state, wind_t_30, wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='medium', pf='mid')
    wind_mid_coal_low_pf_avg_CF = plot_fig_state(wind_mid_coal, state, wind_t_30, wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='medium', pf='low')
    wind_mid_coal_high_pf_high_wacc_avg_LCOE = plot_fig_state(wind_mid_coal_lcoe, state, wind_t_30, 
                                                              wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='medium', pf='high', wacc='high')
    wind_mid_coal_high_pf_mid_wacc_avg_LCOE = plot_fig_state(wind_mid_coal_lcoe, state, wind_t_30, 
                                                             wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='medium', pf='high', wacc='mid')
    wind_mid_coal_high_pf_low_wacc_avg_LCOE = plot_fig_state(wind_mid_coal_lcoe, state, wind_t_30, 
                                                             wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='medium', pf='high', wacc='low')
    wind_mid_coal_mid_pf_high_wacc_avg_LCOE = plot_fig_state(wind_mid_coal_lcoe, state, wind_t_30, 
                                                             wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='medium', pf='mid', wacc='high')
    wind_mid_coal_mid_pf_mid_wacc_avg_LCOE = plot_fig_state(wind_mid_coal_lcoe, state, wind_t_30, 
                                                            wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='medium', pf='mid', wacc='mid')
    wind_mid_coal_mid_pf_low_wacc_avg_LCOE = plot_fig_state(wind_mid_coal_lcoe, state, wind_t_30, 
                                                            wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='medium', pf='mid', wacc='low')
    wind_mid_coal_low_pf_high_wacc_avg_LCOE = plot_fig_state(wind_mid_coal_lcoe, state, wind_t_30, 
                                                             wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='medium', pf='low', wacc='high')
    wind_mid_coal_low_pf_mid_wacc_avg_LCOE = plot_fig_state(wind_mid_coal_lcoe, state, wind_t_30, 
                                                            wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='medium', pf='low', wacc='mid')
    wind_mid_coal_low_pf_low_wacc_avg_LCOE = plot_fig_state(wind_mid_coal_lcoe, state, wind_t_30, 
                                                            wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='medium', pf='low', wacc='low')        
    solar_low_coal_high_pf_avg_CF = plot_fig_state(solar_low_coal, state, solar_t_30, solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='low', pf='high')
    solar_low_coal_mid_pf_avg_CF = plot_fig_state(solar_low_coal, state, solar_t_30, solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='low', pf='mid')
    solar_low_coal_low_pf_avg_CF = plot_fig_state(solar_low_coal, state, solar_t_30, solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='low', pf='low')
    solar_low_coal_high_pf_high_wacc_avg_LCOE = plot_fig_state(solar_low_coal_lcoe, state, solar_t_30, 
                                                               solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='low', pf='high', wacc='high')
    solar_low_coal_high_pf_mid_wacc_avg_LCOE = plot_fig_state(solar_low_coal_lcoe, state, solar_t_30, 
                                                              solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='low', pf='high', wacc='mid')
    solar_low_coal_high_pf_low_wacc_avg_LCOE = plot_fig_state(solar_low_coal_lcoe, state, solar_t_30, 
                                                              solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='low', pf='high', wacc='low')
    solar_low_coal_mid_pf_high_wacc_avg_LCOE = plot_fig_state(solar_low_coal_lcoe, state, solar_t_30, 
                                                              solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='low', pf='mid', wacc='high')
    solar_low_coal_mid_pf_mid_wacc_avg_LCOE = plot_fig_state(solar_low_coal_lcoe, state, solar_t_30, 
                                                             solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='low', pf='mid', wacc='mid')
    solar_low_coal_mid_pf_low_wacc_avg_LCOE = plot_fig_state(solar_low_coal_lcoe, state, solar_t_30, 
                                                             solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='low', pf='mid', wacc='low')
    solar_low_coal_low_pf_high_wacc_avg_LCOE = plot_fig_state(solar_low_coal_lcoe, state, solar_t_30, 
                                                              solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='low', pf='low', wacc='high')
    solar_low_coal_low_pf_mid_wacc_avg_LCOE = plot_fig_state(solar_low_coal_lcoe, state, solar_t_30, 
                                                             solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='low', pf='low', wacc='mid')
    solar_low_coal_low_pf_low_wacc_avg_LCOE = plot_fig_state(solar_low_coal_lcoe, state, solar_t_30, 
                                                             solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='low', pf='low', wacc='low')
    wind_low_coal_high_pf_avg_CF = plot_fig_state(wind_low_coal, state, wind_t_30, wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='low', pf='high')
    wind_low_coal_mid_pf_avg_CF = plot_fig_state(wind_low_coal, state, wind_t_30, wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='low', pf='mid')
    wind_low_coal_low_pf_avg_CF = plot_fig_state(wind_low_coal, state, wind_t_30, wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='low', pf='low')
    wind_low_coal_high_pf_high_wacc_avg_LCOE = plot_fig_state(wind_low_coal_lcoe, state, wind_t_30, 
                                                              wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='low', pf='high', wacc='high')
    wind_low_coal_high_pf_mid_wacc_avg_LCOE = plot_fig_state(wind_low_coal_lcoe, state, wind_t_30, 
                                                             wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='low', pf='high', wacc='mid')
    wind_low_coal_high_pf_low_wacc_avg_LCOE = plot_fig_state(wind_low_coal_lcoe, state, wind_t_30, 
                                                             wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='low', pf='high', wacc='low')
    wind_low_coal_mid_pf_high_wacc_avg_LCOE = plot_fig_state(wind_low_coal_lcoe, state, wind_t_30, 
                                                             wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='low', pf='mid', wacc='high')
    wind_low_coal_mid_pf_mid_wacc_avg_LCOE = plot_fig_state(wind_low_coal_lcoe, state, wind_t_30, 
                                                            wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='low', pf='mid', wacc='mid')
    wind_low_coal_mid_pf_low_wacc_avg_LCOE = plot_fig_state(wind_low_coal_lcoe, state, wind_t_30, 
                                                            wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='low', pf='mid', wacc='low')
    wind_low_coal_low_pf_high_wacc_avg_LCOE = plot_fig_state(wind_low_coal_lcoe, state, wind_t_30, 
                                                             wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='low', pf='low', wacc='high')
    wind_low_coal_low_pf_mid_wacc_avg_LCOE = plot_fig_state(wind_low_coal_lcoe, state, wind_t_30, 
                                                            wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='low', pf='low', wacc='mid')
    wind_low_coal_low_pf_low_wacc_avg_LCOE = plot_fig_state(wind_low_coal_lcoe, state, wind_t_30, 
                                                            wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='low', pf='low', wacc='low')   
    
    solar_all_coal_high_pf_avg_CF = plot_fig_state(solar_all_coal, state, solar_t_30, solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='all', pf='high')
    solar_all_coal_mid_pf_avg_CF = plot_fig_state(solar_all_coal, state, solar_t_30, solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='all', pf='mid')
    solar_all_coal_low_pf_avg_CF = plot_fig_state(solar_all_coal, state, solar_t_30, solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='all', pf='low')
    solar_all_coal_high_pf_high_wacc_avg_LCOE = plot_fig_state(solar_all_coal_lcoe, state, solar_t_30, 
                                                               solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='all', pf='high', wacc='high')
    solar_all_coal_high_pf_mid_wacc_avg_LCOE = plot_fig_state(solar_all_coal_lcoe, state, solar_t_30, 
                                                              solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='all', pf='high', wacc='mid')
    solar_all_coal_high_pf_low_wacc_avg_LCOE = plot_fig_state(solar_all_coal_lcoe, state, solar_t_30, 
                                                              solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='all', pf='high', wacc='low')
    solar_all_coal_mid_pf_high_wacc_avg_LCOE = plot_fig_state(solar_all_coal_lcoe, state, solar_t_30, 
                                                              solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='all', pf='mid', wacc='high')
    solar_all_coal_mid_pf_mid_wacc_avg_LCOE = plot_fig_state(solar_all_coal_lcoe, state, solar_t_30, 
                                                             solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='all', pf='mid', wacc='mid')
    solar_all_coal_mid_pf_low_wacc_avg_LCOE = plot_fig_state(solar_all_coal_lcoe, state, solar_t_30, 
                                                             solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='all', pf='mid', wacc='low')
    solar_all_coal_low_pf_high_wacc_avg_LCOE = plot_fig_state(solar_all_coal_lcoe, state, solar_t_30, 
                                                              solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='all', pf='low', wacc='high')
    solar_all_coal_low_pf_mid_wacc_avg_LCOE = plot_fig_state(solar_all_coal_lcoe, state, solar_t_30, 
                                                             solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='all', pf='low', wacc='mid')
    solar_all_coal_low_pf_low_wacc_avg_LCOE = plot_fig_state(solar_all_coal_lcoe, state, solar_t_30, 
                                                             solar_t_50_base, solar_t_50_lc, 
                                                   col='solar', coal='all', pf='low', wacc='low')
    wind_all_coal_high_pf_avg_CF = plot_fig_state(wind_all_coal, state, wind_t_30, wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='all', pf='high')
    wind_all_coal_mid_pf_avg_CF = plot_fig_state(wind_all_coal, state, wind_t_30, wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='all', pf='mid')
    wind_all_coal_low_pf_avg_CF = plot_fig_state(wind_all_coal, state, wind_t_30, wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='all', pf='low')
    wind_all_coal_high_pf_high_wacc_avg_LCOE = plot_fig_state(wind_all_coal_lcoe, state, wind_t_30, 
                                                              wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='all', pf='high', wacc='high')
    wind_all_coal_high_pf_mid_wacc_avg_LCOE = plot_fig_state(wind_all_coal_lcoe, state, wind_t_30, 
                                                             wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='all', pf='high', wacc='mid')
    wind_all_coal_high_pf_low_wacc_avg_LCOE = plot_fig_state(wind_all_coal_lcoe, state, wind_t_30, 
                                                             wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='all', pf='high', wacc='low')
    wind_all_coal_mid_pf_high_wacc_avg_LCOE = plot_fig_state(wind_all_coal_lcoe, state, wind_t_30,
                                                             wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='all', pf='mid', wacc='high')
    wind_all_coal_mid_pf_mid_wacc_avg_LCOE = plot_fig_state(wind_all_coal_lcoe, state, wind_t_30, 
                                                            wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='all', pf='mid', wacc='mid')
    wind_all_coal_mid_pf_low_wacc_avg_LCOE = plot_fig_state(wind_all_coal_lcoe, state, wind_t_30, 
                                                            wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='all', pf='mid', wacc='low')
    wind_all_coal_low_pf_high_wacc_avg_LCOE = plot_fig_state(wind_all_coal_lcoe, state, wind_t_30,
                                                             wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='all', pf='low', wacc='high')
    wind_all_coal_low_pf_mid_wacc_avg_LCOE = plot_fig_state(wind_all_coal_lcoe, state, wind_t_30, 
                                                            wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='all', pf='low', wacc='mid')
    wind_all_coal_low_pf_low_wacc_avg_LCOE = plot_fig_state(wind_all_coal_lcoe, state, wind_t_30, 
                                                            wind_t_50_base, wind_t_50_lc, 
                                                   col='wind', coal='all', pf='low', wacc='low')        

    if solar_t_30[state] > 0: 
        averages_solar_2030[state] = [
            solar_high_coal_high_pf_avg_CF[0], solar_mid_coal_high_pf_avg_CF[0], 
            solar_low_coal_high_pf_avg_CF[0], solar_all_coal_high_pf_avg_CF[0],
            solar_high_coal_mid_pf_avg_CF[0], solar_mid_coal_mid_pf_avg_CF[0], 
            solar_low_coal_mid_pf_avg_CF[0], solar_all_coal_mid_pf_avg_CF[0],
            solar_high_coal_low_pf_avg_CF[0], solar_mid_coal_low_pf_avg_CF[0], 
            solar_low_coal_low_pf_avg_CF[0], solar_all_coal_low_pf_avg_CF[0],
            solar_high_coal_high_pf_high_wacc_avg_LCOE[0], solar_mid_coal_high_pf_high_wacc_avg_LCOE[0], 
            solar_low_coal_high_pf_high_wacc_avg_LCOE[0], solar_all_coal_high_pf_high_wacc_avg_LCOE[0],
            solar_high_coal_high_pf_mid_wacc_avg_LCOE[0], solar_mid_coal_high_pf_mid_wacc_avg_LCOE[0], 
            solar_low_coal_high_pf_mid_wacc_avg_LCOE[0], solar_all_coal_high_pf_mid_wacc_avg_LCOE[0],
            solar_high_coal_high_pf_low_wacc_avg_LCOE[0], solar_mid_coal_high_pf_low_wacc_avg_LCOE[0], 
            solar_low_coal_high_pf_low_wacc_avg_LCOE[0], solar_all_coal_high_pf_low_wacc_avg_LCOE[0],
            solar_high_coal_mid_pf_high_wacc_avg_LCOE[0], solar_mid_coal_mid_pf_high_wacc_avg_LCOE[0], 
            solar_low_coal_mid_pf_high_wacc_avg_LCOE[0], solar_all_coal_mid_pf_high_wacc_avg_LCOE[0],
            solar_high_coal_mid_pf_mid_wacc_avg_LCOE[0], solar_mid_coal_mid_pf_mid_wacc_avg_LCOE[0], 
            solar_low_coal_mid_pf_mid_wacc_avg_LCOE[0], solar_all_coal_mid_pf_mid_wacc_avg_LCOE[0],
            solar_high_coal_mid_pf_low_wacc_avg_LCOE[0], solar_mid_coal_mid_pf_low_wacc_avg_LCOE[0], 
            solar_low_coal_mid_pf_low_wacc_avg_LCOE[0], solar_all_coal_mid_pf_low_wacc_avg_LCOE[0],
            solar_high_coal_low_pf_high_wacc_avg_LCOE[0], solar_mid_coal_low_pf_high_wacc_avg_LCOE[0], 
            solar_low_coal_low_pf_high_wacc_avg_LCOE[0], solar_all_coal_low_pf_high_wacc_avg_LCOE[0],
            solar_high_coal_low_pf_mid_wacc_avg_LCOE[0], solar_mid_coal_low_pf_mid_wacc_avg_LCOE[0], 
            solar_low_coal_low_pf_mid_wacc_avg_LCOE[0], solar_all_coal_low_pf_mid_wacc_avg_LCOE[0],
            solar_high_coal_low_pf_low_wacc_avg_LCOE[0], solar_mid_coal_low_pf_low_wacc_avg_LCOE[0], 
            solar_low_coal_low_pf_low_wacc_avg_LCOE[0], solar_all_coal_low_pf_low_wacc_avg_LCOE[0]
        ]
                
        averages_solar_2050_base[state] = [
            solar_high_coal_high_pf_avg_CF[1], solar_mid_coal_high_pf_avg_CF[1], 
            solar_low_coal_high_pf_avg_CF[1], solar_all_coal_high_pf_avg_CF[1],
            solar_high_coal_mid_pf_avg_CF[1], solar_mid_coal_mid_pf_avg_CF[1], 
            solar_low_coal_mid_pf_avg_CF[1], solar_all_coal_mid_pf_avg_CF[1],
            solar_high_coal_low_pf_avg_CF[1], solar_mid_coal_low_pf_avg_CF[1], 
            solar_low_coal_low_pf_avg_CF[1], solar_all_coal_low_pf_avg_CF[1],
            solar_high_coal_high_pf_high_wacc_avg_LCOE[1], solar_mid_coal_high_pf_high_wacc_avg_LCOE[1], 
            solar_low_coal_high_pf_high_wacc_avg_LCOE[1], solar_all_coal_high_pf_high_wacc_avg_LCOE[1],
            solar_high_coal_high_pf_mid_wacc_avg_LCOE[1], solar_mid_coal_high_pf_mid_wacc_avg_LCOE[1], 
            solar_low_coal_high_pf_mid_wacc_avg_LCOE[1], solar_all_coal_high_pf_mid_wacc_avg_LCOE[1],
            solar_high_coal_high_pf_low_wacc_avg_LCOE[1], solar_mid_coal_high_pf_low_wacc_avg_LCOE[1], 
            solar_low_coal_high_pf_low_wacc_avg_LCOE[1], solar_all_coal_high_pf_low_wacc_avg_LCOE[1],
            solar_high_coal_mid_pf_high_wacc_avg_LCOE[1], solar_mid_coal_mid_pf_high_wacc_avg_LCOE[1], 
            solar_low_coal_mid_pf_high_wacc_avg_LCOE[1], solar_all_coal_mid_pf_high_wacc_avg_LCOE[1],
            solar_high_coal_mid_pf_mid_wacc_avg_LCOE[1], solar_mid_coal_mid_pf_mid_wacc_avg_LCOE[1], 
            solar_low_coal_mid_pf_mid_wacc_avg_LCOE[1], solar_all_coal_mid_pf_mid_wacc_avg_LCOE[1],
            solar_high_coal_mid_pf_low_wacc_avg_LCOE[1], solar_mid_coal_mid_pf_low_wacc_avg_LCOE[1], 
            solar_low_coal_mid_pf_low_wacc_avg_LCOE[1], solar_all_coal_mid_pf_low_wacc_avg_LCOE[1],
            solar_high_coal_low_pf_high_wacc_avg_LCOE[1], solar_mid_coal_low_pf_high_wacc_avg_LCOE[1], 
            solar_low_coal_low_pf_high_wacc_avg_LCOE[1], solar_all_coal_low_pf_high_wacc_avg_LCOE[1],
            solar_high_coal_low_pf_mid_wacc_avg_LCOE[1], solar_mid_coal_low_pf_mid_wacc_avg_LCOE[1], 
            solar_low_coal_low_pf_mid_wacc_avg_LCOE[1], solar_all_coal_low_pf_mid_wacc_avg_LCOE[1],
            solar_high_coal_low_pf_low_wacc_avg_LCOE[1], solar_mid_coal_low_pf_low_wacc_avg_LCOE[1], 
            solar_low_coal_low_pf_low_wacc_avg_LCOE[1], solar_all_coal_low_pf_low_wacc_avg_LCOE[1]
        ]
        
        averages_solar_2050_lc[state] = [
            solar_high_coal_high_pf_avg_CF[2], solar_mid_coal_high_pf_avg_CF[2], 
            solar_low_coal_high_pf_avg_CF[2], solar_all_coal_high_pf_avg_CF[2],
            solar_high_coal_mid_pf_avg_CF[2], solar_mid_coal_mid_pf_avg_CF[2], 
            solar_low_coal_mid_pf_avg_CF[2], solar_all_coal_mid_pf_avg_CF[2],
            solar_high_coal_low_pf_avg_CF[2], solar_mid_coal_low_pf_avg_CF[2], 
            solar_low_coal_low_pf_avg_CF[2], solar_all_coal_low_pf_avg_CF[2],
            solar_high_coal_high_pf_high_wacc_avg_LCOE[2], solar_mid_coal_high_pf_high_wacc_avg_LCOE[2], 
            solar_low_coal_high_pf_high_wacc_avg_LCOE[2], solar_all_coal_high_pf_high_wacc_avg_LCOE[2],
            solar_high_coal_high_pf_mid_wacc_avg_LCOE[2], solar_mid_coal_high_pf_mid_wacc_avg_LCOE[2], 
            solar_low_coal_high_pf_mid_wacc_avg_LCOE[2], solar_all_coal_high_pf_mid_wacc_avg_LCOE[2],
            solar_high_coal_high_pf_low_wacc_avg_LCOE[2], solar_mid_coal_high_pf_low_wacc_avg_LCOE[2], 
            solar_low_coal_high_pf_low_wacc_avg_LCOE[2], solar_all_coal_high_pf_low_wacc_avg_LCOE[2],
            solar_high_coal_mid_pf_high_wacc_avg_LCOE[2], solar_mid_coal_mid_pf_high_wacc_avg_LCOE[2], 
            solar_low_coal_mid_pf_high_wacc_avg_LCOE[2], solar_all_coal_mid_pf_high_wacc_avg_LCOE[2],
            solar_high_coal_mid_pf_mid_wacc_avg_LCOE[2], solar_mid_coal_mid_pf_mid_wacc_avg_LCOE[2], 
            solar_low_coal_mid_pf_mid_wacc_avg_LCOE[2], solar_all_coal_mid_pf_mid_wacc_avg_LCOE[2],
            solar_high_coal_mid_pf_low_wacc_avg_LCOE[2], solar_mid_coal_mid_pf_low_wacc_avg_LCOE[2], 
            solar_low_coal_mid_pf_low_wacc_avg_LCOE[2], solar_all_coal_mid_pf_low_wacc_avg_LCOE[2],
            solar_high_coal_low_pf_high_wacc_avg_LCOE[2], solar_mid_coal_low_pf_high_wacc_avg_LCOE[2], 
            solar_low_coal_low_pf_high_wacc_avg_LCOE[2], solar_all_coal_low_pf_high_wacc_avg_LCOE[2],
            solar_high_coal_low_pf_mid_wacc_avg_LCOE[2], solar_mid_coal_low_pf_mid_wacc_avg_LCOE[2], 
            solar_low_coal_low_pf_mid_wacc_avg_LCOE[2], solar_all_coal_low_pf_mid_wacc_avg_LCOE[2],
            solar_high_coal_low_pf_low_wacc_avg_LCOE[2], solar_mid_coal_low_pf_low_wacc_avg_LCOE[2], 
            solar_low_coal_low_pf_low_wacc_avg_LCOE[2], solar_all_coal_low_pf_low_wacc_avg_LCOE[2]
        ]
        
        if solar_high_coal_mid_pf_avg_CF[3] is not np.nan:
            high_capacities['solar_2030'][state] = solar_high_coal_mid_pf_avg_CF[3]['cumsum mid'].max()
            all_capacities['solar_2030'][state] = solar_all_coal_mid_pf_avg_CF[3]['cumsum mid'].max()
        if solar_high_coal_mid_pf_avg_CF[4] is not np.nan:
            high_capacities['solar_2050_base'][state] = solar_high_coal_mid_pf_avg_CF[4]['cumsum mid'].max()
            all_capacities['solar_2050_base'][state] = solar_all_coal_mid_pf_avg_CF[4]['cumsum mid'].max()
        if solar_high_coal_mid_pf_avg_CF[5] is not np.nan:
            high_capacities['solar_2050_lc'][state] = solar_high_coal_mid_pf_avg_CF[5]['cumsum mid'].max() 
            all_capacities['solar_2050_lc'][state] = solar_all_coal_mid_pf_avg_CF[5]['cumsum mid'].max()             
        
    if wind_t_30[state] > 0: 
        averages_wind_2030[state] = [
            wind_high_coal_high_pf_avg_CF[0], wind_mid_coal_high_pf_avg_CF[0], 
            wind_low_coal_high_pf_avg_CF[0], wind_all_coal_high_pf_avg_CF[0],
            wind_high_coal_mid_pf_avg_CF[0], wind_mid_coal_mid_pf_avg_CF[0], 
            wind_low_coal_mid_pf_avg_CF[0], wind_all_coal_mid_pf_avg_CF[0],
            wind_high_coal_low_pf_avg_CF[0], wind_mid_coal_low_pf_avg_CF[0], 
            wind_low_coal_low_pf_avg_CF[0], wind_all_coal_low_pf_avg_CF[0],
            wind_high_coal_high_pf_high_wacc_avg_LCOE[0], wind_mid_coal_high_pf_high_wacc_avg_LCOE[0], 
            wind_low_coal_high_pf_high_wacc_avg_LCOE[0], wind_all_coal_high_pf_high_wacc_avg_LCOE[0],
            wind_high_coal_high_pf_mid_wacc_avg_LCOE[0], wind_mid_coal_high_pf_mid_wacc_avg_LCOE[0], 
            wind_low_coal_high_pf_mid_wacc_avg_LCOE[0], wind_all_coal_high_pf_mid_wacc_avg_LCOE[0],
            wind_high_coal_high_pf_low_wacc_avg_LCOE[0], wind_mid_coal_high_pf_low_wacc_avg_LCOE[0], 
            wind_low_coal_high_pf_low_wacc_avg_LCOE[0], wind_all_coal_high_pf_low_wacc_avg_LCOE[0],
            wind_high_coal_mid_pf_high_wacc_avg_LCOE[0], wind_mid_coal_mid_pf_high_wacc_avg_LCOE[0], 
            wind_low_coal_mid_pf_high_wacc_avg_LCOE[0], wind_all_coal_mid_pf_high_wacc_avg_LCOE[0],
            wind_high_coal_mid_pf_mid_wacc_avg_LCOE[0], wind_mid_coal_mid_pf_mid_wacc_avg_LCOE[0], 
            wind_low_coal_mid_pf_mid_wacc_avg_LCOE[0], wind_all_coal_mid_pf_mid_wacc_avg_LCOE[0],
            wind_high_coal_mid_pf_low_wacc_avg_LCOE[0], wind_mid_coal_mid_pf_low_wacc_avg_LCOE[0], 
            wind_low_coal_mid_pf_low_wacc_avg_LCOE[0], wind_all_coal_mid_pf_low_wacc_avg_LCOE[0],
            wind_high_coal_low_pf_high_wacc_avg_LCOE[0], wind_mid_coal_low_pf_high_wacc_avg_LCOE[0], 
            wind_low_coal_low_pf_high_wacc_avg_LCOE[0], wind_all_coal_low_pf_high_wacc_avg_LCOE[0],
            wind_high_coal_low_pf_mid_wacc_avg_LCOE[0], wind_mid_coal_low_pf_mid_wacc_avg_LCOE[0], 
            wind_low_coal_low_pf_mid_wacc_avg_LCOE[0], wind_all_coal_low_pf_mid_wacc_avg_LCOE[0],
            wind_high_coal_low_pf_low_wacc_avg_LCOE[0], wind_mid_coal_low_pf_low_wacc_avg_LCOE[0], 
            wind_low_coal_low_pf_low_wacc_avg_LCOE[0], wind_all_coal_low_pf_low_wacc_avg_LCOE[0]
        ]
        
        averages_wind_2050_base[state] = [
            wind_high_coal_high_pf_avg_CF[1], wind_mid_coal_high_pf_avg_CF[1], 
            wind_low_coal_high_pf_avg_CF[1], wind_all_coal_high_pf_avg_CF[1],
            wind_high_coal_mid_pf_avg_CF[1], wind_mid_coal_mid_pf_avg_CF[1], 
            wind_low_coal_mid_pf_avg_CF[1], wind_all_coal_mid_pf_avg_CF[1],
            wind_high_coal_low_pf_avg_CF[1], wind_mid_coal_low_pf_avg_CF[1], 
            wind_low_coal_low_pf_avg_CF[1], wind_all_coal_low_pf_avg_CF[1],
            wind_high_coal_high_pf_high_wacc_avg_LCOE[1], wind_mid_coal_high_pf_high_wacc_avg_LCOE[1], 
            wind_low_coal_high_pf_high_wacc_avg_LCOE[1], wind_all_coal_high_pf_high_wacc_avg_LCOE[1],
            wind_high_coal_high_pf_mid_wacc_avg_LCOE[1], wind_mid_coal_high_pf_mid_wacc_avg_LCOE[1], 
            wind_low_coal_high_pf_mid_wacc_avg_LCOE[1], wind_all_coal_high_pf_mid_wacc_avg_LCOE[1],
            wind_high_coal_high_pf_low_wacc_avg_LCOE[1], wind_mid_coal_high_pf_low_wacc_avg_LCOE[1], 
            wind_low_coal_high_pf_low_wacc_avg_LCOE[1], wind_all_coal_high_pf_low_wacc_avg_LCOE[1],
            wind_high_coal_mid_pf_high_wacc_avg_LCOE[1], wind_mid_coal_mid_pf_high_wacc_avg_LCOE[1], 
            wind_low_coal_mid_pf_high_wacc_avg_LCOE[1], wind_all_coal_mid_pf_high_wacc_avg_LCOE[1],
            wind_high_coal_mid_pf_mid_wacc_avg_LCOE[1], wind_mid_coal_mid_pf_mid_wacc_avg_LCOE[1], 
            wind_low_coal_mid_pf_mid_wacc_avg_LCOE[1], wind_all_coal_mid_pf_mid_wacc_avg_LCOE[1],
            wind_high_coal_mid_pf_low_wacc_avg_LCOE[1], wind_mid_coal_mid_pf_low_wacc_avg_LCOE[1], 
            wind_low_coal_mid_pf_low_wacc_avg_LCOE[1], wind_all_coal_mid_pf_low_wacc_avg_LCOE[1],
            wind_high_coal_low_pf_high_wacc_avg_LCOE[1], wind_mid_coal_low_pf_high_wacc_avg_LCOE[1], 
            wind_low_coal_low_pf_high_wacc_avg_LCOE[1], wind_all_coal_low_pf_high_wacc_avg_LCOE[1],
            wind_high_coal_low_pf_mid_wacc_avg_LCOE[1], wind_mid_coal_low_pf_mid_wacc_avg_LCOE[1], 
            wind_low_coal_low_pf_mid_wacc_avg_LCOE[1], wind_all_coal_low_pf_mid_wacc_avg_LCOE[1],
            wind_high_coal_low_pf_low_wacc_avg_LCOE[1], wind_mid_coal_low_pf_low_wacc_avg_LCOE[1], 
            wind_low_coal_low_pf_low_wacc_avg_LCOE[1], wind_all_coal_low_pf_low_wacc_avg_LCOE[1]
        ]
        
        averages_wind_2050_lc[state] = [
            wind_high_coal_high_pf_avg_CF[2], wind_mid_coal_high_pf_avg_CF[2], 
            wind_low_coal_high_pf_avg_CF[2], wind_all_coal_high_pf_avg_CF[2],
            wind_high_coal_mid_pf_avg_CF[2], wind_mid_coal_mid_pf_avg_CF[2], 
            wind_low_coal_mid_pf_avg_CF[2], wind_all_coal_mid_pf_avg_CF[2],
            wind_high_coal_low_pf_avg_CF[2], wind_mid_coal_low_pf_avg_CF[2], 
            wind_low_coal_low_pf_avg_CF[2], wind_all_coal_low_pf_avg_CF[2],
            wind_high_coal_high_pf_high_wacc_avg_LCOE[2], wind_mid_coal_high_pf_high_wacc_avg_LCOE[2], 
            wind_low_coal_high_pf_high_wacc_avg_LCOE[2], wind_all_coal_high_pf_high_wacc_avg_LCOE[2],
            wind_high_coal_high_pf_mid_wacc_avg_LCOE[2], wind_mid_coal_high_pf_mid_wacc_avg_LCOE[2], 
            wind_low_coal_high_pf_mid_wacc_avg_LCOE[2], wind_all_coal_high_pf_mid_wacc_avg_LCOE[2],
            wind_high_coal_high_pf_low_wacc_avg_LCOE[2], wind_mid_coal_high_pf_low_wacc_avg_LCOE[2], 
            wind_low_coal_high_pf_low_wacc_avg_LCOE[2], wind_all_coal_high_pf_low_wacc_avg_LCOE[2],
            wind_high_coal_mid_pf_high_wacc_avg_LCOE[2], wind_mid_coal_mid_pf_high_wacc_avg_LCOE[2], 
            wind_low_coal_mid_pf_high_wacc_avg_LCOE[2], wind_all_coal_mid_pf_high_wacc_avg_LCOE[2],
            wind_high_coal_mid_pf_mid_wacc_avg_LCOE[2], wind_mid_coal_mid_pf_mid_wacc_avg_LCOE[2], 
            wind_low_coal_mid_pf_mid_wacc_avg_LCOE[2], wind_all_coal_mid_pf_mid_wacc_avg_LCOE[2],
            wind_high_coal_mid_pf_low_wacc_avg_LCOE[2], wind_mid_coal_mid_pf_low_wacc_avg_LCOE[2], 
            wind_low_coal_mid_pf_low_wacc_avg_LCOE[2], wind_all_coal_mid_pf_low_wacc_avg_LCOE[2],
            wind_high_coal_low_pf_high_wacc_avg_LCOE[2], wind_mid_coal_low_pf_high_wacc_avg_LCOE[2], 
            wind_low_coal_low_pf_high_wacc_avg_LCOE[2], wind_all_coal_low_pf_high_wacc_avg_LCOE[2],
            wind_high_coal_low_pf_mid_wacc_avg_LCOE[2], wind_mid_coal_low_pf_mid_wacc_avg_LCOE[2], 
            wind_low_coal_low_pf_mid_wacc_avg_LCOE[2], wind_all_coal_low_pf_mid_wacc_avg_LCOE[2],
            wind_high_coal_low_pf_low_wacc_avg_LCOE[2], wind_mid_coal_low_pf_low_wacc_avg_LCOE[2], 
            wind_low_coal_low_pf_low_wacc_avg_LCOE[2], wind_all_coal_low_pf_low_wacc_avg_LCOE[2]
        ]
        
        if wind_high_coal_mid_pf_avg_CF[3] is not np.nan:
            high_capacities['wind_2030'][state] = wind_high_coal_mid_pf_avg_CF[3]['cumsum mid'].max()
            all_capacities['wind_2030'][state] = wind_all_coal_mid_pf_avg_CF[3]['cumsum mid'].max()
        if wind_high_coal_mid_pf_avg_CF[4] is not np.nan:
            high_capacities['wind_2050_base'][state] = wind_high_coal_mid_pf_avg_CF[4]['cumsum mid'].max()
            all_capacities['wind_2050_base'][state] = wind_all_coal_mid_pf_avg_CF[4]['cumsum mid'].max()
        if wind_high_coal_mid_pf_avg_CF[5] is not np.nan:
            high_capacities['wind_2050_lc'][state] = wind_high_coal_mid_pf_avg_CF[5]['cumsum mid'].max() 
            all_capacities['wind_2050_lc'][state] = wind_all_coal_mid_pf_avg_CF[5]['cumsum mid'].max() 

In [10]:
pd.DataFrame(high_capacities)

wind_2030  solar_2030  wind_2050_base  \
Gujarat                      13.442375   16.470005       46.996056   
Jammu and Kashmir             0.000000    0.000000        0.000000   
Arunachal Pradesh             0.000000    0.000000        0.000000   
Assam                         0.000000    0.000000        0.000000   
Sikkim                        0.000000    0.000000        0.000000   
West Bengal                   2.293618   11.563038        7.927180   
Uttarakhand                   0.000000    0.000000        0.000000   
Uttar Pradesh                 4.635728   15.920269       15.399514   
Bihar                         2.767781   14.870724        8.036492   
Nagaland                      0.000000    0.000000        0.000000   
Manipur                       0.000000    0.000000        0.000000   
Mizoram                       0.000000    0.000000        0.000000   
Tripura                       0.000000    0.000000        0.000000   
Meghalaya                     0.000000    0.000000        0.000000   
Punjab                        0.522795    0.000000        6.141031   
Rajasthan                    12.561627   16.287493       45.178007   
Himachal Pradesh              0.000000    0.000000        0.000000   
Andhra Pradesh                8.038302    7.720107       25.620634   
Odisha                        1.966571   13.061520        8.697266   
Daman and Diu                 0.000000    0.000000        0.000000   
Maharashtra                  10.404532   17.840514       38.878762   
Goa                           0.000000    0.000000        0.000000   
Karnataka                    14.712402   10.511408       51.831097   
Kerala                        0.000000    0.000000        0.000000   
Puducherry                    0.000000    0.000000        0.000000   
Tamil Nadu                   13.803677   26.319825       46.650136   
Lakshadweep                   0.000000    0.000000        0.000000   
Andaman and Nicobar Islands   0.000000    0.000000        0.000000   
Jharkhand                     5.145180    7.495067       14.890815   
Delhi                         0.000000    0.000000        0.000000   
Dadra and Nagar Haveli        0.000000    0.000000        0.000000   
Chandigarh                    0.000000    0.000000        0.000000   
Madhya Pradesh               13.145131   15.174585       42.913700   
Chhattisgarh                  5.434202   13.443942       17.790104   
Haryana                       4.960242    0.000000       16.534741   
Telangana                     6.912348   16.445024       28.425369   

                             solar_2050_base  wind_2050_lc  solar_2050_lc  
Gujarat                            36.205098     56.658542     121.365543  
Jammu and Kashmir                   0.000000      0.000000       0.000000  
Arunachal Pradesh                   0.000000      0.000000       0.000000  
Assam                               0.000000      0.000000       0.000000  
Sikkim                              0.000000      0.000000       0.000000  
West Bengal                        21.435794     11.192652       0.000000  
Uttarakhand                         0.000000      0.000000       0.000000  
Uttar Pradesh                      28.731089     19.722951       0.000000  
Bihar                               0.000000     12.877166       0.000000  
Nagaland                            0.000000      0.000000       0.000000  
Manipur                             0.000000      0.000000       0.000000  
Mizoram                             0.000000      0.000000       0.000000  
Tripura                             0.000000      0.000000       0.000000  
Meghalaya                           0.000000      0.000000       0.000000  
Punjab                              0.000000      8.463616       0.000000  
Rajasthan                          37.761052     54.308684     140.165379  
Himachal Pradesh                    0.000000      0.000000       0.000000  
Andhra Pradesh                     20.982469     34.201629      61.520

In [11]:
# export to pickle
os.chdir('../tables')
filehandler = open("high_capacities.pickle","wb")
pickle.dump(pd.DataFrame(high_capacities), filehandler)
filehandler.close()
filehandler = open("all_capacities.pickle","wb")
pickle.dump(pd.DataFrame(all_capacities), filehandler)
filehandler.close()

In [12]:
# make state pivot tables
pivot_solar_2030 = pd.DataFrame(averages_solar_2030).T
pivot_solar_2030.columns = [
    'solar_high_coal_high_pf_avg_CF', 'solar_mid_coal_high_pf_avg_CF', 
    'solar_low_coal_high_pf_avg_CF', 'solar_all_coal_high_pf_avg_CF', 
    'solar_high_coal_mid_pf_avg_CF', 'solar_mid_coal_mid_pf_avg_CF', 
    'solar_low_coal_mid_pf_avg_CF', 'solar_all_coal_mid_pf_avg_CF',
    'solar_high_coal_low_pf_avg_CF', 'solar_mid_coal_low_pf_avg_CF', 
    'solar_low_coal_low_pf_avg_CF', 'solar_all_coal_low_pf_avg_CF',
    'solar_high_coal_high_pf_high_wacc_avg_LCOE', 'solar_mid_coal_high_pf_high_wacc_avg_LCOE', 
    'solar_low_coal_high_pf_high_wacc_avg_LCOE', 'solar_all_coal_high_pf_high_wacc_avg_LCOE',
    'solar_high_coal_high_pf_mid_wacc_avg_LCOE', 'solar_mid_coal_high_pf_mid_wacc_avg_LCOE', 
    'solar_low_coal_high_pf_mid_wacc_avg_LCOE', 'solar_all_coal_high_pf_mid_wacc_avg_LCOE',
    'solar_high_coal_high_pf_low_wacc_avg_LCOE', 'solar_mid_coal_high_pf_low_wacc_avg_LCOE', 
    'solar_low_coal_high_pf_low_wacc_avg_LCOE', 'solar_all_coal_high_pf_low_wacc_avg_LCOE',
    'solar_high_coal_mid_pf_high_wacc_avg_LCOE', 'solar_mid_coal_mid_pf_high_wacc_avg_LCOE', 
    'solar_low_coal_mid_pf_high_wacc_avg_LCOE', 'solar_all_coal_mid_pf_high_wacc_avg_LCOE',
    'solar_high_coal_mid_pf_mid_wacc_avg_LCOE', 'solar_mid_coal_mid_pf_mid_wacc_avg_LCOE', 
    'solar_low_coal_mid_pf_mid_wacc_avg_LCOE', 'solar_all_coal_mid_pf_mid_wacc_avg_LCOE',
    'solar_high_coal_mid_pf_low_wacc_avg_LCOE', 'solar_mid_coal_mid_pf_low_wacc_avg_LCOE', 
    'solar_low_coal_mid_pf_low_wacc_avg_LCOE', 'solar_all_coal_mid_pf_low_wacc_avg_LCOE',
    'solar_high_coal_low_pf_high_wacc_avg_LCOE', 'solar_mid_coal_low_pf_high_wacc_avg_LCOE', 
    'solar_low_coal_low_pf_high_wacc_avg_LCOE', 'solar_all_coal_low_pf_high_wacc_avg_LCOE',
    'solar_high_coal_low_pf_mid_wacc_avg_LCOE', 'solar_mid_coal_low_pf_mid_wacc_avg_LCOE', 
    'solar_low_coal_low_pf_mid_wacc_avg_LCOE', 'solar_all_coal_low_pf_mid_wacc_avg_LCOE',
    'solar_high_coal_low_pf_low_wacc_avg_LCOE', 'solar_mid_coal_low_pf_low_wacc_avg_LCOE', 
    'solar_low_coal_low_pf_low_wacc_avg_LCOE', 'solar_all_coal_low_pf_low_wacc_avg_LCOE'
]

pivot_solar_2050_base = pd.DataFrame(averages_solar_2050_base).T
pivot_solar_2050_base.columns = [
    'solar_high_coal_high_pf_avg_CF', 'solar_mid_coal_high_pf_avg_CF', 
    'solar_low_coal_high_pf_avg_CF', 'solar_all_coal_high_pf_avg_CF', 
    'solar_high_coal_mid_pf_avg_CF', 'solar_mid_coal_mid_pf_avg_CF', 
    'solar_low_coal_mid_pf_avg_CF', 'solar_all_coal_mid_pf_avg_CF',
    'solar_high_coal_low_pf_avg_CF', 'solar_mid_coal_low_pf_avg_CF', 
    'solar_low_coal_low_pf_avg_CF', 'solar_all_coal_low_pf_avg_CF',
    'solar_high_coal_high_pf_high_wacc_avg_LCOE', 'solar_mid_coal_high_pf_high_wacc_avg_LCOE', 
    'solar_low_coal_high_pf_high_wacc_avg_LCOE', 'solar_all_coal_high_pf_high_wacc_avg_LCOE',
    'solar_high_coal_high_pf_mid_wacc_avg_LCOE', 'solar_mid_coal_high_pf_mid_wacc_avg_LCOE', 
    'solar_low_coal_high_pf_mid_wacc_avg_LCOE', 'solar_all_coal_high_pf_mid_wacc_avg_LCOE',
    'solar_high_coal_high_pf_low_wacc_avg_LCOE', 'solar_mid_coal_high_pf_low_wacc_avg_LCOE', 
    'solar_low_coal_high_pf_low_wacc_avg_LCOE', 'solar_all_coal_high_pf_low_wacc_avg_LCOE',
    'solar_high_coal_mid_pf_high_wacc_avg_LCOE', 'solar_mid_coal_mid_pf_high_wacc_avg_LCOE', 
    'solar_low_coal_mid_pf_high_wacc_avg_LCOE', 'solar_all_coal_mid_pf_high_wacc_avg_LCOE',
    'solar_high_coal_mid_pf_mid_wacc_avg_LCOE', 'solar_mid_coal_mid_pf_mid_wacc_avg_LCOE', 
    'solar_low_coal_mid_pf_mid_wacc_avg_LCOE', 'solar_all_coal_mid_pf_mid_wacc_avg_LCOE',
    'solar_high_coal_mid_pf_low_wacc_avg_LCOE', 'solar_mid_coal_mid_pf_low_wacc_avg_LCOE', 
    'solar_low_coal_mid_pf_low_wacc_avg_LCOE', 'solar_all_coal_mid_pf_low_wacc_avg_LCOE',
    'solar_high_coal_low_pf_high_wacc_avg_LCOE', 'solar_mid_coal_low_pf_high_wacc_avg_LCOE', 
    'solar_low_coal_low_pf_high_wacc_avg_LCOE', 'solar_all_coal_low_pf_high_wacc_avg_LCOE',
    'solar_high_coal_low_pf_mid_wacc_avg_LCOE', 'solar_mid_coal_low_pf_mid_wacc_avg_LCOE', 
    'solar_low_coal_low_pf_mid_wacc_avg_LCOE', 'solar_all_coal_low_pf_mid_wacc_avg_LCOE',
    'solar_high_coal_low_pf_low_wacc_avg_LCOE', 'solar_mid_coal_low_pf_low_wacc_avg_LCOE', 
    'solar_low_coal_low_pf_low_wacc_avg_LCOE', 'solar_all_coal_low_pf_low_wacc_avg_LCOE'
]

pivot_solar_2050_lc = pd.DataFrame(averages_solar_2050_lc).T
pivot_solar_2050_lc.columns = [
    'solar_high_coal_high_pf_avg_CF', 'solar_mid_coal_high_pf_avg_CF', 
    'solar_low_coal_high_pf_avg_CF', 'solar_all_coal_high_pf_avg_CF', 
    'solar_high_coal_mid_pf_avg_CF', 'solar_mid_coal_mid_pf_avg_CF', 
    'solar_low_coal_mid_pf_avg_CF', 'solar_all_coal_mid_pf_avg_CF',
    'solar_high_coal_low_pf_avg_CF', 'solar_mid_coal_low_pf_avg_CF', 
    'solar_low_coal_low_pf_avg_CF', 'solar_all_coal_low_pf_avg_CF',
    'solar_high_coal_high_pf_high_wacc_avg_LCOE', 'solar_mid_coal_high_pf_high_wacc_avg_LCOE', 
    'solar_low_coal_high_pf_high_wacc_avg_LCOE', 'solar_all_coal_high_pf_high_wacc_avg_LCOE',
    'solar_high_coal_high_pf_mid_wacc_avg_LCOE', 'solar_mid_coal_high_pf_mid_wacc_avg_LCOE', 
    'solar_low_coal_high_pf_mid_wacc_avg_LCOE', 'solar_all_coal_high_pf_mid_wacc_avg_LCOE',
    'solar_high_coal_high_pf_low_wacc_avg_LCOE', 'solar_mid_coal_high_pf_low_wacc_avg_LCOE', 
    'solar_low_coal_high_pf_low_wacc_avg_LCOE', 'solar_all_coal_high_pf_low_wacc_avg_LCOE',
    'solar_high_coal_mid_pf_high_wacc_avg_LCOE', 'solar_mid_coal_mid_pf_high_wacc_avg_LCOE', 
    'solar_low_coal_mid_pf_high_wacc_avg_LCOE', 'solar_all_coal_mid_pf_high_wacc_avg_LCOE',
    'solar_high_coal_mid_pf_mid_wacc_avg_LCOE', 'solar_mid_coal_mid_pf_mid_wacc_avg_LCOE', 
    'solar_low_coal_mid_pf_mid_wacc_avg_LCOE', 'solar_all_coal_mid_pf_mid_wacc_avg_LCOE',
    'solar_high_coal_mid_pf_low_wacc_avg_LCOE', 'solar_mid_coal_mid_pf_low_wacc_avg_LCOE', 
    'solar_low_coal_mid_pf_low_wacc_avg_LCOE', 'solar_all_coal_mid_pf_low_wacc_avg_LCOE',
    'solar_high_coal_low_pf_high_wacc_avg_LCOE', 'solar_mid_coal_low_pf_high_wacc_avg_LCOE', 
    'solar_low_coal_low_pf_high_wacc_avg_LCOE', 'solar_all_coal_low_pf_high_wacc_avg_LCOE',
    'solar_high_coal_low_pf_mid_wacc_avg_LCOE', 'solar_mid_coal_low_pf_mid_wacc_avg_LCOE', 
    'solar_low_coal_low_pf_mid_wacc_avg_LCOE', 'solar_all_coal_low_pf_mid_wacc_avg_LCOE',
    'solar_high_coal_low_pf_low_wacc_avg_LCOE', 'solar_mid_coal_low_pf_low_wacc_avg_LCOE', 
    'solar_low_coal_low_pf_low_wacc_avg_LCOE', 'solar_all_coal_low_pf_low_wacc_avg_LCOE'
]

pivot_wind_2030 = pd.DataFrame(averages_wind_2030).T
pivot_wind_2030.columns = [
    'wind_high_coal_high_pf_avg_CF', 'wind_mid_coal_high_pf_avg_CF', 
    'wind_low_coal_high_pf_avg_CF', 'wind_all_coal_high_pf_avg_CF', 
    'wind_high_coal_mid_pf_avg_CF', 'wind_mid_coal_mid_pf_avg_CF', 
    'wind_low_coal_mid_pf_avg_CF', 'wind_all_coal_mid_pf_avg_CF',
    'wind_high_coal_low_pf_avg_CF', 'wind_mid_coal_low_pf_avg_CF', 
    'wind_low_coal_low_pf_avg_CF', 'wind_all_coal_low_pf_avg_CF',
    'wind_high_coal_high_pf_high_wacc_avg_LCOE', 'wind_mid_coal_high_pf_high_wacc_avg_LCOE', 
    'wind_low_coal_high_pf_high_wacc_avg_LCOE', 'wind_all_coal_high_pf_high_wacc_avg_LCOE',
    'wind_high_coal_high_pf_mid_wacc_avg_LCOE', 'wind_mid_coal_high_pf_mid_wacc_avg_LCOE', 
    'wind_low_coal_high_pf_mid_wacc_avg_LCOE', 'wind_all_coal_high_pf_mid_wacc_avg_LCOE',
    'wind_high_coal_high_pf_low_wacc_avg_LCOE', 'wind_mid_coal_high_pf_low_wacc_avg_LCOE', 
    'wind_low_coal_high_pf_low_wacc_avg_LCOE', 'wind_all_coal_high_pf_low_wacc_avg_LCOE',
    'wind_high_coal_mid_pf_high_wacc_avg_LCOE', 'wind_mid_coal_mid_pf_high_wacc_avg_LCOE', 
    'wind_low_coal_mid_pf_high_wacc_avg_LCOE', 'wind_all_coal_mid_pf_high_wacc_avg_LCOE',
    'wind_high_coal_mid_pf_mid_wacc_avg_LCOE', 'wind_mid_coal_mid_pf_mid_wacc_avg_LCOE', 
    'wind_low_coal_mid_pf_mid_wacc_avg_LCOE', 'wind_all_coal_mid_pf_mid_wacc_avg_LCOE',
    'wind_high_coal_mid_pf_low_wacc_avg_LCOE', 'wind_mid_coal_mid_pf_low_wacc_avg_LCOE', 
    'wind_low_coal_mid_pf_low_wacc_avg_LCOE', 'wind_all_coal_mid_pf_low_wacc_avg_LCOE',
    'wind_high_coal_low_pf_high_wacc_avg_LCOE', 'wind_mid_coal_low_pf_high_wacc_avg_LCOE', 
    'wind_low_coal_low_pf_high_wacc_avg_LCOE', 'wind_all_coal_low_pf_high_wacc_avg_LCOE',
    'wind_high_coal_low_pf_mid_wacc_avg_LCOE', 'wind_mid_coal_low_pf_mid_wacc_avg_LCOE', 
    'wind_low_coal_low_pf_mid_wacc_avg_LCOE', 'wind_all_coal_low_pf_mid_wacc_avg_LCOE',
    'wind_high_coal_low_pf_low_wacc_avg_LCOE', 'wind_mid_coal_low_pf_low_wacc_avg_LCOE', 
    'wind_low_coal_low_pf_low_wacc_avg_LCOE', 'wind_all_coal_low_pf_low_wacc_avg_LCOE'
]

pivot_wind_2050_base = pd.DataFrame(averages_wind_2050_base).T
pivot_wind_2050_base.columns = [
    'wind_high_coal_high_pf_avg_CF', 'wind_mid_coal_high_pf_avg_CF', 
    'wind_low_coal_high_pf_avg_CF', 'wind_all_coal_high_pf_avg_CF', 
    'wind_high_coal_mid_pf_avg_CF', 'wind_mid_coal_mid_pf_avg_CF', 
    'wind_low_coal_mid_pf_avg_CF', 'wind_all_coal_mid_pf_avg_CF',
    'wind_high_coal_low_pf_avg_CF', 'wind_mid_coal_low_pf_avg_CF', 
    'wind_low_coal_low_pf_avg_CF', 'wind_all_coal_low_pf_avg_CF',
    'wind_high_coal_high_pf_high_wacc_avg_LCOE', 'wind_mid_coal_high_pf_high_wacc_avg_LCOE', 
    'wind_low_coal_high_pf_high_wacc_avg_LCOE', 'wind_all_coal_high_pf_high_wacc_avg_LCOE',
    'wind_high_coal_high_pf_mid_wacc_avg_LCOE', 'wind_mid_coal_high_pf_mid_wacc_avg_LCOE', 
    'wind_low_coal_high_pf_mid_wacc_avg_LCOE', 'wind_all_coal_high_pf_mid_wacc_avg_LCOE',
    'wind_high_coal_high_pf_low_wacc_avg_LCOE', 'wind_mid_coal_high_pf_low_wacc_avg_LCOE', 
    'wind_low_coal_high_pf_low_wacc_avg_LCOE', 'wind_all_coal_high_pf_low_wacc_avg_LCOE',
    'wind_high_coal_mid_pf_high_wacc_avg_LCOE', 'wind_mid_coal_mid_pf_high_wacc_avg_LCOE', 
    'wind_low_coal_mid_pf_high_wacc_avg_LCOE', 'wind_all_coal_mid_pf_high_wacc_avg_LCOE',
    'wind_high_coal_mid_pf_mid_wacc_avg_LCOE', 'wind_mid_coal_mid_pf_mid_wacc_avg_LCOE', 
    'wind_low_coal_mid_pf_mid_wacc_avg_LCOE', 'wind_all_coal_mid_pf_mid_wacc_avg_LCOE',
    'wind_high_coal_mid_pf_low_wacc_avg_LCOE', 'wind_mid_coal_mid_pf_low_wacc_avg_LCOE', 
    'wind_low_coal_mid_pf_low_wacc_avg_LCOE', 'wind_all_coal_mid_pf_low_wacc_avg_LCOE',
    'wind_high_coal_low_pf_high_wacc_avg_LCOE', 'wind_mid_coal_low_pf_high_wacc_avg_LCOE', 
    'wind_low_coal_low_pf_high_wacc_avg_LCOE', 'wind_all_coal_low_pf_high_wacc_avg_LCOE',
    'wind_high_coal_low_pf_mid_wacc_avg_LCOE', 'wind_mid_coal_low_pf_mid_wacc_avg_LCOE', 
    'wind_low_coal_low_pf_mid_wacc_avg_LCOE', 'wind_all_coal_low_pf_mid_wacc_avg_LCOE',
    'wind_high_coal_low_pf_low_wacc_avg_LCOE', 'wind_mid_coal_low_pf_low_wacc_avg_LCOE', 
    'wind_low_coal_low_pf_low_wacc_avg_LCOE', 'wind_all_coal_low_pf_low_wacc_avg_LCOE'
]

pivot_wind_2050_lc = pd.DataFrame(averages_wind_2050_lc).T
pivot_wind_2050_lc.columns = [
    'wind_high_coal_high_pf_avg_CF', 'wind_mid_coal_high_pf_avg_CF', 
    'wind_low_coal_high_pf_avg_CF', 'wind_all_coal_high_pf_avg_CF', 
    'wind_high_coal_mid_pf_avg_CF', 'wind_mid_coal_mid_pf_avg_CF', 
    'wind_low_coal_mid_pf_avg_CF', 'wind_all_coal_mid_pf_avg_CF',
    'wind_high_coal_low_pf_avg_CF', 'wind_mid_coal_low_pf_avg_CF', 
    'wind_low_coal_low_pf_avg_CF', 'wind_all_coal_low_pf_avg_CF',
    'wind_high_coal_high_pf_high_wacc_avg_LCOE', 'wind_mid_coal_high_pf_high_wacc_avg_LCOE', 
    'wind_low_coal_high_pf_high_wacc_avg_LCOE', 'wind_all_coal_high_pf_high_wacc_avg_LCOE',
    'wind_high_coal_high_pf_mid_wacc_avg_LCOE', 'wind_mid_coal_high_pf_mid_wacc_avg_LCOE', 
    'wind_low_coal_high_pf_mid_wacc_avg_LCOE', 'wind_all_coal_high_pf_mid_wacc_avg_LCOE',
    'wind_high_coal_high_pf_low_wacc_avg_LCOE', 'wind_mid_coal_high_pf_low_wacc_avg_LCOE', 
    'wind_low_coal_high_pf_low_wacc_avg_LCOE', 'wind_all_coal_high_pf_low_wacc_avg_LCOE',
    'wind_high_coal_mid_pf_high_wacc_avg_LCOE', 'wind_mid_coal_mid_pf_high_wacc_avg_LCOE', 
    'wind_low_coal_mid_pf_high_wacc_avg_LCOE', 'wind_all_coal_mid_pf_high_wacc_avg_LCOE',
    'wind_high_coal_mid_pf_mid_wacc_avg_LCOE', 'wind_mid_coal_mid_pf_mid_wacc_avg_LCOE', 
    'wind_low_coal_mid_pf_mid_wacc_avg_LCOE', 'wind_all_coal_mid_pf_mid_wacc_avg_LCOE',
    'wind_high_coal_mid_pf_low_wacc_avg_LCOE', 'wind_mid_coal_mid_pf_low_wacc_avg_LCOE', 
    'wind_low_coal_mid_pf_low_wacc_avg_LCOE', 'wind_all_coal_mid_pf_low_wacc_avg_LCOE',
    'wind_high_coal_low_pf_high_wacc_avg_LCOE', 'wind_mid_coal_low_pf_high_wacc_avg_LCOE', 
    'wind_low_coal_low_pf_high_wacc_avg_LCOE', 'wind_all_coal_low_pf_high_wacc_avg_LCOE',
    'wind_high_coal_low_pf_mid_wacc_avg_LCOE', 'wind_mid_coal_low_pf_mid_wacc_avg_LCOE', 
    'wind_low_coal_low_pf_mid_wacc_avg_LCOE', 'wind_all_coal_low_pf_mid_wacc_avg_LCOE',
    'wind_high_coal_low_pf_low_wacc_avg_LCOE', 'wind_mid_coal_low_pf_low_wacc_avg_LCOE', 
    'wind_low_coal_low_pf_low_wacc_avg_LCOE', 'wind_all_coal_low_pf_low_wacc_avg_LCOE'
]

In [13]:
# break down into smaller dataframes
solar_high_cf_summary_30 = pivot_solar_2030[
    ['solar_high_coal_high_pf_avg_CF',  'solar_high_coal_mid_pf_avg_CF', 'solar_high_coal_low_pf_avg_CF']
]
solar_high_cf_summary_30.columns = ['High PF', 'Medium PF', 'Low PF']

solar_mid_cf_summary_30 = pivot_solar_2030[
    ['solar_mid_coal_high_pf_avg_CF',  'solar_mid_coal_mid_pf_avg_CF', 'solar_mid_coal_low_pf_avg_CF']
]
solar_mid_cf_summary_30.columns = ['High PF', 'Medium PF', 'Low PF']

solar_low_cf_summary_30 = pivot_solar_2030[
    ['solar_low_coal_high_pf_avg_CF',  'solar_low_coal_mid_pf_avg_CF', 'solar_low_coal_low_pf_avg_CF']
]
solar_low_cf_summary_30.columns = ['High PF', 'Medium PF', 'Low PF']

solar_all_cf_summary_30 = pivot_solar_2030[
    ['solar_all_coal_high_pf_avg_CF',  'solar_all_coal_mid_pf_avg_CF', 'solar_all_coal_low_pf_avg_CF']
]
solar_all_cf_summary_30.columns = ['High PF', 'Medium PF', 'Low PF']

solar_high_lcoe_summary_30 = pivot_solar_2030[
    ['solar_high_coal_high_pf_high_wacc_avg_LCOE', 'solar_high_coal_high_pf_mid_wacc_avg_LCOE', 
     'solar_high_coal_high_pf_low_wacc_avg_LCOE', 
     'solar_high_coal_mid_pf_high_wacc_avg_LCOE', 'solar_high_coal_mid_pf_mid_wacc_avg_LCOE', 
     'solar_high_coal_mid_pf_low_wacc_avg_LCOE', 
     'solar_high_coal_low_pf_high_wacc_avg_LCOE', 'solar_high_coal_low_pf_mid_wacc_avg_LCOE', 
     'solar_high_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
solar_high_lcoe_summary_30.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

solar_mid_lcoe_summary_30 = pivot_solar_2030[
    ['solar_mid_coal_high_pf_high_wacc_avg_LCOE', 'solar_mid_coal_high_pf_mid_wacc_avg_LCOE', 
     'solar_mid_coal_high_pf_low_wacc_avg_LCOE', 
     'solar_mid_coal_mid_pf_high_wacc_avg_LCOE', 'solar_mid_coal_mid_pf_mid_wacc_avg_LCOE', 
     'solar_mid_coal_mid_pf_low_wacc_avg_LCOE', 
     'solar_mid_coal_low_pf_high_wacc_avg_LCOE', 'solar_mid_coal_low_pf_mid_wacc_avg_LCOE', 
     'solar_mid_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
solar_mid_lcoe_summary_30.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

solar_low_lcoe_summary_30 = pivot_solar_2030[
    ['solar_low_coal_high_pf_high_wacc_avg_LCOE', 'solar_low_coal_high_pf_mid_wacc_avg_LCOE', 
     'solar_low_coal_high_pf_low_wacc_avg_LCOE', 
     'solar_low_coal_mid_pf_high_wacc_avg_LCOE', 'solar_low_coal_mid_pf_mid_wacc_avg_LCOE', 
     'solar_low_coal_mid_pf_low_wacc_avg_LCOE', 
     'solar_low_coal_low_pf_high_wacc_avg_LCOE', 'solar_low_coal_low_pf_mid_wacc_avg_LCOE', 
     'solar_low_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
solar_low_lcoe_summary_30.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

solar_all_lcoe_summary_30 = pivot_solar_2030[
    ['solar_all_coal_high_pf_high_wacc_avg_LCOE', 'solar_all_coal_high_pf_mid_wacc_avg_LCOE', 
     'solar_all_coal_high_pf_low_wacc_avg_LCOE', 
     'solar_all_coal_mid_pf_high_wacc_avg_LCOE', 'solar_all_coal_mid_pf_mid_wacc_avg_LCOE', 
     'solar_all_coal_mid_pf_low_wacc_avg_LCOE', 
     'solar_all_coal_low_pf_high_wacc_avg_LCOE', 'solar_all_coal_low_pf_mid_wacc_avg_LCOE', 
     'solar_all_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
solar_all_lcoe_summary_30.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']


wind_high_cf_summary_30 = pivot_wind_2030[
    ['wind_high_coal_high_pf_avg_CF',  'wind_high_coal_mid_pf_avg_CF', 'wind_high_coal_low_pf_avg_CF']
]
wind_high_cf_summary_30.columns = ['High PF', 'Medium PF', 'Low PF']

wind_mid_cf_summary_30 = pivot_wind_2030[
    ['wind_mid_coal_high_pf_avg_CF',  'wind_mid_coal_mid_pf_avg_CF', 'wind_mid_coal_low_pf_avg_CF']
]
wind_mid_cf_summary_30.columns = ['High PF', 'Medium PF', 'Low PF']

wind_low_cf_summary_30 = pivot_wind_2030[
    ['wind_low_coal_high_pf_avg_CF',  'wind_low_coal_mid_pf_avg_CF', 'wind_low_coal_low_pf_avg_CF']
]
wind_low_cf_summary_30.columns = ['High PF', 'Medium PF', 'Low PF']

wind_all_cf_summary_30 = pivot_wind_2030[
    ['wind_all_coal_high_pf_avg_CF',  'wind_all_coal_mid_pf_avg_CF', 'wind_all_coal_low_pf_avg_CF']
]
wind_all_cf_summary_30.columns = ['High PF', 'Medium PF', 'Low PF']

wind_high_lcoe_summary_30 = pivot_wind_2030[
    ['wind_high_coal_high_pf_high_wacc_avg_LCOE', 'wind_high_coal_high_pf_mid_wacc_avg_LCOE', 
     'wind_high_coal_high_pf_low_wacc_avg_LCOE', 
     'wind_high_coal_mid_pf_high_wacc_avg_LCOE', 'wind_high_coal_mid_pf_mid_wacc_avg_LCOE', 
     'wind_high_coal_mid_pf_low_wacc_avg_LCOE', 
     'wind_high_coal_low_pf_high_wacc_avg_LCOE', 'wind_high_coal_low_pf_mid_wacc_avg_LCOE', 
     'wind_high_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
wind_high_lcoe_summary_30.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

wind_mid_lcoe_summary_30 = pivot_wind_2030[
    ['wind_mid_coal_high_pf_high_wacc_avg_LCOE', 'wind_mid_coal_high_pf_mid_wacc_avg_LCOE', 
     'wind_mid_coal_high_pf_low_wacc_avg_LCOE', 
     'wind_mid_coal_mid_pf_high_wacc_avg_LCOE', 'wind_mid_coal_mid_pf_mid_wacc_avg_LCOE', 
     'wind_mid_coal_mid_pf_low_wacc_avg_LCOE', 
     'wind_mid_coal_low_pf_high_wacc_avg_LCOE', 'wind_mid_coal_low_pf_mid_wacc_avg_LCOE', 
     'wind_mid_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
wind_mid_lcoe_summary_30.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

wind_low_lcoe_summary_30 = pivot_wind_2030[
    ['wind_low_coal_high_pf_high_wacc_avg_LCOE', 'wind_low_coal_high_pf_mid_wacc_avg_LCOE', 
     'wind_low_coal_high_pf_low_wacc_avg_LCOE', 
     'wind_low_coal_mid_pf_high_wacc_avg_LCOE', 'wind_low_coal_mid_pf_mid_wacc_avg_LCOE', 
     'wind_low_coal_mid_pf_low_wacc_avg_LCOE', 
     'wind_low_coal_low_pf_high_wacc_avg_LCOE', 'wind_low_coal_low_pf_mid_wacc_avg_LCOE', 
     'wind_low_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
wind_low_lcoe_summary_30.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

wind_all_lcoe_summary_30 = pivot_wind_2030[
    ['wind_all_coal_high_pf_high_wacc_avg_LCOE', 'wind_all_coal_high_pf_mid_wacc_avg_LCOE', 
     'wind_all_coal_high_pf_low_wacc_avg_LCOE', 
     'wind_all_coal_mid_pf_high_wacc_avg_LCOE', 'wind_all_coal_mid_pf_mid_wacc_avg_LCOE', 
     'wind_all_coal_mid_pf_low_wacc_avg_LCOE', 
     'wind_all_coal_low_pf_high_wacc_avg_LCOE', 'wind_all_coal_low_pf_mid_wacc_avg_LCOE', 
     'wind_all_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
wind_all_lcoe_summary_30.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

In [14]:
# break down into smaller dataframes
solar_high_cf_summary_50_base = pivot_solar_2050_base[
    ['solar_high_coal_high_pf_avg_CF',  'solar_high_coal_mid_pf_avg_CF', 'solar_high_coal_low_pf_avg_CF']
]
solar_high_cf_summary_50_base.columns = ['High PF', 'Medium PF', 'Low PF']

solar_mid_cf_summary_50_base = pivot_solar_2050_base[
    ['solar_mid_coal_high_pf_avg_CF',  'solar_mid_coal_mid_pf_avg_CF', 'solar_mid_coal_low_pf_avg_CF']
]
solar_mid_cf_summary_50_base.columns = ['High PF', 'Medium PF', 'Low PF']

solar_low_cf_summary_50_base = pivot_solar_2050_base[
    ['solar_low_coal_high_pf_avg_CF',  'solar_low_coal_mid_pf_avg_CF', 'solar_low_coal_low_pf_avg_CF']
]
solar_low_cf_summary_50_base.columns = ['High PF', 'Medium PF', 'Low PF']

solar_all_cf_summary_50_base = pivot_solar_2050_base[
    ['solar_all_coal_high_pf_avg_CF',  'solar_all_coal_mid_pf_avg_CF', 'solar_all_coal_low_pf_avg_CF']
]
solar_all_cf_summary_50_base.columns = ['High PF', 'Medium PF', 'Low PF']

solar_high_lcoe_summary_50_base = pivot_solar_2050_base[
    ['solar_high_coal_high_pf_high_wacc_avg_LCOE', 'solar_high_coal_high_pf_mid_wacc_avg_LCOE', 
     'solar_high_coal_high_pf_low_wacc_avg_LCOE', 
     'solar_high_coal_mid_pf_high_wacc_avg_LCOE', 'solar_high_coal_mid_pf_mid_wacc_avg_LCOE', 
     'solar_high_coal_mid_pf_low_wacc_avg_LCOE', 
     'solar_high_coal_low_pf_high_wacc_avg_LCOE', 'solar_high_coal_low_pf_mid_wacc_avg_LCOE', 
     'solar_high_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
solar_high_lcoe_summary_50_base.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

solar_mid_lcoe_summary_50_base = pivot_solar_2050_base[
    ['solar_mid_coal_high_pf_high_wacc_avg_LCOE', 'solar_mid_coal_high_pf_mid_wacc_avg_LCOE', 
     'solar_mid_coal_high_pf_low_wacc_avg_LCOE', 
     'solar_mid_coal_mid_pf_high_wacc_avg_LCOE', 'solar_mid_coal_mid_pf_mid_wacc_avg_LCOE', 
     'solar_mid_coal_mid_pf_low_wacc_avg_LCOE', 
     'solar_mid_coal_low_pf_high_wacc_avg_LCOE', 'solar_mid_coal_low_pf_mid_wacc_avg_LCOE', 
     'solar_mid_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
solar_mid_lcoe_summary_50_base.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

solar_low_lcoe_summary_50_base = pivot_solar_2050_base[
    ['solar_low_coal_high_pf_high_wacc_avg_LCOE', 'solar_low_coal_high_pf_mid_wacc_avg_LCOE', 
     'solar_low_coal_high_pf_low_wacc_avg_LCOE', 
     'solar_low_coal_mid_pf_high_wacc_avg_LCOE', 'solar_low_coal_mid_pf_mid_wacc_avg_LCOE', 
     'solar_low_coal_mid_pf_low_wacc_avg_LCOE', 
     'solar_low_coal_low_pf_high_wacc_avg_LCOE', 'solar_low_coal_low_pf_mid_wacc_avg_LCOE', 
     'solar_low_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
solar_low_lcoe_summary_50_base.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

solar_all_lcoe_summary_50_base = pivot_solar_2050_base[
    ['solar_all_coal_high_pf_high_wacc_avg_LCOE', 'solar_all_coal_high_pf_mid_wacc_avg_LCOE', 
     'solar_all_coal_high_pf_low_wacc_avg_LCOE', 
     'solar_all_coal_mid_pf_high_wacc_avg_LCOE', 'solar_all_coal_mid_pf_mid_wacc_avg_LCOE', 
     'solar_all_coal_mid_pf_low_wacc_avg_LCOE', 
     'solar_all_coal_low_pf_high_wacc_avg_LCOE', 'solar_all_coal_low_pf_mid_wacc_avg_LCOE', 
     'solar_all_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
solar_all_lcoe_summary_50_base.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']


wind_high_cf_summary_50_base = pivot_wind_2050_base[
    ['wind_high_coal_high_pf_avg_CF',  'wind_high_coal_mid_pf_avg_CF', 'wind_high_coal_low_pf_avg_CF']
]
wind_high_cf_summary_50_base.columns = ['High PF', 'Medium PF', 'Low PF']

wind_mid_cf_summary_50_base = pivot_wind_2050_base[
    ['wind_mid_coal_high_pf_avg_CF',  'wind_mid_coal_mid_pf_avg_CF', 'wind_mid_coal_low_pf_avg_CF']
]
wind_mid_cf_summary_50_base.columns = ['High PF', 'Medium PF', 'Low PF']

wind_low_cf_summary_50_base = pivot_wind_2050_base[
    ['wind_low_coal_high_pf_avg_CF',  'wind_low_coal_mid_pf_avg_CF', 'wind_low_coal_low_pf_avg_CF']
]
wind_low_cf_summary_50_base.columns = ['High PF', 'Medium PF', 'Low PF']

wind_all_cf_summary_50_base = pivot_wind_2050_base[
    ['wind_all_coal_high_pf_avg_CF',  'wind_all_coal_mid_pf_avg_CF', 'wind_all_coal_low_pf_avg_CF']
]
wind_all_cf_summary_50_base.columns = ['High PF', 'Medium PF', 'Low PF']

wind_high_lcoe_summary_50_base = pivot_wind_2050_base[
    ['wind_high_coal_high_pf_high_wacc_avg_LCOE', 'wind_high_coal_high_pf_mid_wacc_avg_LCOE', 
     'wind_high_coal_high_pf_low_wacc_avg_LCOE', 
     'wind_high_coal_mid_pf_high_wacc_avg_LCOE', 'wind_high_coal_mid_pf_mid_wacc_avg_LCOE', 
     'wind_high_coal_mid_pf_low_wacc_avg_LCOE', 
     'wind_high_coal_low_pf_high_wacc_avg_LCOE', 'wind_high_coal_low_pf_mid_wacc_avg_LCOE', 
     'wind_high_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
wind_high_lcoe_summary_50_base.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

wind_mid_lcoe_summary_50_base = pivot_wind_2050_base[
    ['wind_mid_coal_high_pf_high_wacc_avg_LCOE', 'wind_mid_coal_high_pf_mid_wacc_avg_LCOE', 
     'wind_mid_coal_high_pf_low_wacc_avg_LCOE', 
     'wind_mid_coal_mid_pf_high_wacc_avg_LCOE', 'wind_mid_coal_mid_pf_mid_wacc_avg_LCOE', 
     'wind_mid_coal_mid_pf_low_wacc_avg_LCOE', 
     'wind_mid_coal_low_pf_high_wacc_avg_LCOE', 'wind_mid_coal_low_pf_mid_wacc_avg_LCOE', 
     'wind_mid_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
wind_mid_lcoe_summary_50_base.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

wind_low_lcoe_summary_50_base = pivot_wind_2050_base[
    ['wind_low_coal_high_pf_high_wacc_avg_LCOE', 'wind_low_coal_high_pf_mid_wacc_avg_LCOE', 
     'wind_low_coal_high_pf_low_wacc_avg_LCOE', 
     'wind_low_coal_mid_pf_high_wacc_avg_LCOE', 'wind_low_coal_mid_pf_mid_wacc_avg_LCOE', 
     'wind_low_coal_mid_pf_low_wacc_avg_LCOE', 
     'wind_low_coal_low_pf_high_wacc_avg_LCOE', 'wind_low_coal_low_pf_mid_wacc_avg_LCOE', 
     'wind_low_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
wind_low_lcoe_summary_50_base.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

wind_all_lcoe_summary_50_base = pivot_wind_2050_base[
    ['wind_all_coal_high_pf_high_wacc_avg_LCOE', 'wind_all_coal_high_pf_mid_wacc_avg_LCOE', 
     'wind_all_coal_high_pf_low_wacc_avg_LCOE', 
     'wind_all_coal_mid_pf_high_wacc_avg_LCOE', 'wind_all_coal_mid_pf_mid_wacc_avg_LCOE', 
     'wind_all_coal_mid_pf_low_wacc_avg_LCOE', 
     'wind_all_coal_low_pf_high_wacc_avg_LCOE', 'wind_all_coal_low_pf_mid_wacc_avg_LCOE', 
     'wind_all_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
wind_all_lcoe_summary_50_base.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

In [15]:
# break down into smaller dataframes
solar_high_cf_summary_50_lc = pivot_solar_2050_lc[
    ['solar_high_coal_high_pf_avg_CF',  'solar_high_coal_mid_pf_avg_CF', 'solar_high_coal_low_pf_avg_CF']
]
solar_high_cf_summary_50_lc.columns = ['High PF', 'Medium PF', 'Low PF']

solar_mid_cf_summary_50_lc = pivot_solar_2050_lc[
    ['solar_mid_coal_high_pf_avg_CF',  'solar_mid_coal_mid_pf_avg_CF', 'solar_mid_coal_low_pf_avg_CF']
]
solar_mid_cf_summary_50_lc.columns = ['High PF', 'Medium PF', 'Low PF']

solar_low_cf_summary_50_lc = pivot_solar_2050_lc[
    ['solar_low_coal_high_pf_avg_CF',  'solar_low_coal_mid_pf_avg_CF', 'solar_low_coal_low_pf_avg_CF']
]
solar_low_cf_summary_50_lc.columns = ['High PF', 'Medium PF', 'Low PF']

solar_all_cf_summary_50_lc = pivot_solar_2050_lc[
    ['solar_all_coal_high_pf_avg_CF',  'solar_all_coal_mid_pf_avg_CF', 'solar_all_coal_low_pf_avg_CF']
]
solar_all_cf_summary_50_lc.columns = ['High PF', 'Medium PF', 'Low PF']

solar_high_lcoe_summary_50_lc = pivot_solar_2050_lc[
    ['solar_high_coal_high_pf_high_wacc_avg_LCOE', 'solar_high_coal_high_pf_mid_wacc_avg_LCOE', 
     'solar_high_coal_high_pf_low_wacc_avg_LCOE', 
     'solar_high_coal_mid_pf_high_wacc_avg_LCOE', 'solar_high_coal_mid_pf_mid_wacc_avg_LCOE', 
     'solar_high_coal_mid_pf_low_wacc_avg_LCOE', 
     'solar_high_coal_low_pf_high_wacc_avg_LCOE', 'solar_high_coal_low_pf_mid_wacc_avg_LCOE', 
     'solar_high_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
solar_high_lcoe_summary_50_lc.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

solar_mid_lcoe_summary_50_lc = pivot_solar_2050_lc[
    ['solar_mid_coal_high_pf_high_wacc_avg_LCOE', 'solar_mid_coal_high_pf_mid_wacc_avg_LCOE', 
     'solar_mid_coal_high_pf_low_wacc_avg_LCOE', 
     'solar_mid_coal_mid_pf_high_wacc_avg_LCOE', 'solar_mid_coal_mid_pf_mid_wacc_avg_LCOE', 
     'solar_mid_coal_mid_pf_low_wacc_avg_LCOE', 
     'solar_mid_coal_low_pf_high_wacc_avg_LCOE', 'solar_mid_coal_low_pf_mid_wacc_avg_LCOE', 
     'solar_mid_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
solar_mid_lcoe_summary_50_lc.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

solar_low_lcoe_summary_50_lc = pivot_solar_2050_lc[
    ['solar_low_coal_high_pf_high_wacc_avg_LCOE', 'solar_low_coal_high_pf_mid_wacc_avg_LCOE', 
     'solar_low_coal_high_pf_low_wacc_avg_LCOE', 
     'solar_low_coal_mid_pf_high_wacc_avg_LCOE', 'solar_low_coal_mid_pf_mid_wacc_avg_LCOE', 
     'solar_low_coal_mid_pf_low_wacc_avg_LCOE', 
     'solar_low_coal_low_pf_high_wacc_avg_LCOE', 'solar_low_coal_low_pf_mid_wacc_avg_LCOE', 
     'solar_low_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
solar_low_lcoe_summary_50_lc.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

solar_all_lcoe_summary_50_lc = pivot_solar_2050_lc[
    ['solar_all_coal_high_pf_high_wacc_avg_LCOE', 'solar_all_coal_high_pf_mid_wacc_avg_LCOE', 
     'solar_all_coal_high_pf_low_wacc_avg_LCOE', 
     'solar_all_coal_mid_pf_high_wacc_avg_LCOE', 'solar_all_coal_mid_pf_mid_wacc_avg_LCOE', 
     'solar_all_coal_mid_pf_low_wacc_avg_LCOE', 
     'solar_all_coal_low_pf_high_wacc_avg_LCOE', 'solar_all_coal_low_pf_mid_wacc_avg_LCOE', 
     'solar_all_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
solar_all_lcoe_summary_50_lc.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']


wind_high_cf_summary_50_lc = pivot_wind_2050_lc[
    ['wind_high_coal_high_pf_avg_CF',  'wind_high_coal_mid_pf_avg_CF', 'wind_high_coal_low_pf_avg_CF']
]
wind_high_cf_summary_50_lc.columns = ['High PF', 'Medium PF', 'Low PF']

wind_mid_cf_summary_50_lc = pivot_wind_2050_lc[
    ['wind_mid_coal_high_pf_avg_CF',  'wind_mid_coal_mid_pf_avg_CF', 'wind_mid_coal_low_pf_avg_CF']
]
wind_mid_cf_summary_50_lc.columns = ['High PF', 'Medium PF', 'Low PF']

wind_low_cf_summary_50_lc = pivot_wind_2050_lc[
    ['wind_low_coal_high_pf_avg_CF',  'wind_low_coal_mid_pf_avg_CF', 'wind_low_coal_low_pf_avg_CF']
]
wind_low_cf_summary_50_lc.columns = ['High PF', 'Medium PF', 'Low PF']

wind_all_cf_summary_50_lc = pivot_wind_2050_lc[
    ['wind_all_coal_high_pf_avg_CF',  'wind_all_coal_mid_pf_avg_CF', 'wind_all_coal_low_pf_avg_CF']
]
wind_all_cf_summary_50_lc.columns = ['High PF', 'Medium PF', 'Low PF']

wind_high_lcoe_summary_50_lc = pivot_wind_2050_lc[
    ['wind_high_coal_high_pf_high_wacc_avg_LCOE', 'wind_high_coal_high_pf_mid_wacc_avg_LCOE', 
     'wind_high_coal_high_pf_low_wacc_avg_LCOE', 
     'wind_high_coal_mid_pf_high_wacc_avg_LCOE', 'wind_high_coal_mid_pf_mid_wacc_avg_LCOE', 
     'wind_high_coal_mid_pf_low_wacc_avg_LCOE', 
     'wind_high_coal_low_pf_high_wacc_avg_LCOE', 'wind_high_coal_low_pf_mid_wacc_avg_LCOE', 
     'wind_high_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
wind_high_lcoe_summary_50_lc.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

wind_mid_lcoe_summary_50_lc = pivot_wind_2050_lc[
    ['wind_mid_coal_high_pf_high_wacc_avg_LCOE', 'wind_mid_coal_high_pf_mid_wacc_avg_LCOE', 
     'wind_mid_coal_high_pf_low_wacc_avg_LCOE', 
     'wind_mid_coal_mid_pf_high_wacc_avg_LCOE', 'wind_mid_coal_mid_pf_mid_wacc_avg_LCOE', 
     'wind_mid_coal_mid_pf_low_wacc_avg_LCOE', 
     'wind_mid_coal_low_pf_high_wacc_avg_LCOE', 'wind_mid_coal_low_pf_mid_wacc_avg_LCOE', 
     'wind_mid_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
wind_mid_lcoe_summary_50_lc.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

wind_low_lcoe_summary_50_lc = pivot_wind_2050_lc[
    ['wind_low_coal_high_pf_high_wacc_avg_LCOE', 'wind_low_coal_high_pf_mid_wacc_avg_LCOE', 
     'wind_low_coal_high_pf_low_wacc_avg_LCOE', 
     'wind_low_coal_mid_pf_high_wacc_avg_LCOE', 'wind_low_coal_mid_pf_mid_wacc_avg_LCOE', 
     'wind_low_coal_mid_pf_low_wacc_avg_LCOE', 
     'wind_low_coal_low_pf_high_wacc_avg_LCOE', 'wind_low_coal_low_pf_mid_wacc_avg_LCOE', 
     'wind_low_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
wind_low_lcoe_summary_50_lc.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

wind_all_lcoe_summary_50_lc = pivot_wind_2050_lc[
    ['wind_all_coal_high_pf_high_wacc_avg_LCOE', 'wind_all_coal_high_pf_mid_wacc_avg_LCOE', 
     'wind_all_coal_high_pf_low_wacc_avg_LCOE', 
     'wind_all_coal_mid_pf_high_wacc_avg_LCOE', 'wind_all_coal_mid_pf_mid_wacc_avg_LCOE', 
     'wind_all_coal_mid_pf_low_wacc_avg_LCOE', 
     'wind_all_coal_low_pf_high_wacc_avg_LCOE', 'wind_all_coal_low_pf_mid_wacc_avg_LCOE', 
     'wind_all_coal_low_pf_low_wacc_avg_LCOE'
    ]
]
wind_all_lcoe_summary_50_lc.columns = ['High WACC High PF', 'Medium WACC High PF', 'Low WACC High PF',
                                      'High WACC Medium PF', 'Medium WACC Medium PF', 'Low WACC Medium PF',
                                      'High WACC Low PF', 'Medium WACC Low PF', 'Low WACC Low PF']

In [16]:
os.chdir('../tables')
# export to pickle
filehandler = open("solar_high_cf_summary_30.pickle","wb")
pickle.dump(solar_high_cf_summary_30, filehandler)
filehandler.close()
filehandler = open("solar_mid_cf_summary_30.pickle","wb")
pickle.dump(solar_mid_cf_summary_30, filehandler)
filehandler.close()
filehandler = open("solar_low_cf_summary_30.pickle","wb")
pickle.dump(solar_low_cf_summary_30, filehandler)
filehandler.close()
filehandler = open("solar_all_cf_summary_30.pickle","wb")
pickle.dump(solar_all_cf_summary_30, filehandler)
filehandler.close()
filehandler = open("solar_high_lcoe_summary_30.pickle","wb")
pickle.dump(solar_high_lcoe_summary_30, filehandler)
filehandler.close()
filehandler = open("solar_mid_lcoe_summary_30.pickle","wb")
pickle.dump(solar_mid_lcoe_summary_30, filehandler)
filehandler.close()
filehandler = open("solar_low_lcoe_summary_30.pickle","wb")
pickle.dump(solar_low_lcoe_summary_30, filehandler)
filehandler.close()
filehandler = open("solar_all_lcoe_summary_30.pickle","wb")
pickle.dump(solar_all_lcoe_summary_30, filehandler)
filehandler.close()
filehandler = open("wind_high_cf_summary_30.pickle","wb")
pickle.dump(wind_high_cf_summary_30, filehandler)
filehandler.close()
filehandler = open("wind_mid_cf_summary_30.pickle","wb")
pickle.dump(wind_mid_cf_summary_30, filehandler)
filehandler.close()
filehandler = open("wind_low_cf_summary_30.pickle","wb")
pickle.dump(wind_low_cf_summary_30, filehandler)
filehandler.close()
filehandler = open("wind_all_cf_summary_30.pickle","wb")
pickle.dump(wind_all_cf_summary_30, filehandler)
filehandler.close()
filehandler = open("wind_high_lcoe_summary_30.pickle","wb")
pickle.dump(wind_high_lcoe_summary_30, filehandler)
filehandler.close()
filehandler = open("wind_mid_lcoe_summary_30.pickle","wb")
pickle.dump(wind_mid_lcoe_summary_30, filehandler)
filehandler.close()
filehandler = open("wind_low_lcoe_summary_30.pickle","wb")
pickle.dump(wind_low_lcoe_summary_30, filehandler)
filehandler.close()
filehandler = open("wind_all_lcoe_summary_30.pickle","wb")
pickle.dump(wind_all_lcoe_summary_30, filehandler)
filehandler.close()
filehandler = open("solar_high_cf_summary_50_base.pickle","wb")
pickle.dump(solar_high_cf_summary_50_base, filehandler)
filehandler.close()
filehandler = open("solar_mid_cf_summary_50_base.pickle","wb")
pickle.dump(solar_mid_cf_summary_50_base, filehandler)
filehandler.close()
filehandler = open("solar_low_cf_summary_50_base.pickle","wb")
pickle.dump(solar_low_cf_summary_50_base, filehandler)
filehandler.close()
filehandler = open("solar_all_cf_summary_50_base.pickle","wb")
pickle.dump(solar_all_cf_summary_50_base, filehandler)
filehandler.close()
filehandler = open("solar_high_lcoe_summary_50_base.pickle","wb")
pickle.dump(solar_high_lcoe_summary_50_base, filehandler)
filehandler.close()
filehandler = open("solar_mid_lcoe_summary_50_base.pickle","wb")
pickle.dump(solar_mid_lcoe_summary_50_base, filehandler)
filehandler.close()
filehandler = open("solar_low_lcoe_summary_50_base.pickle","wb")
pickle.dump(solar_low_lcoe_summary_50_base, filehandler)
filehandler.close()
filehandler = open("solar_all_lcoe_summary_50_base.pickle","wb")
pickle.dump(solar_all_lcoe_summary_50_base, filehandler)
filehandler.close()
filehandler = open("wind_high_cf_summary_50_base.pickle","wb")
pickle.dump(wind_high_cf_summary_50_base, filehandler)
filehandler.close()
filehandler = open("wind_mid_cf_summary_50_base.pickle","wb")
pickle.dump(wind_mid_cf_summary_50_base, filehandler)
filehandler.close()
filehandler = open("wind_low_cf_summary_50_base.pickle","wb")
pickle.dump(wind_low_cf_summary_50_base, filehandler)
filehandler.close()
filehandler = open("wind_all_cf_summary_50_base.pickle","wb")
pickle.dump(wind_all_cf_summary_50_base, filehandler)
filehandler.close()
filehandler = open("wind_high_lcoe_summary_50_base.pickle","wb")
pickle.dump(wind_high_lcoe_summary_50_base, filehandler)
filehandler.close()
filehandler = open("wind_mid_lcoe_summary_50_base.pickle","wb")
pickle.dump(wind_mid_lcoe_summary_50_base, filehandler)
filehandler.close()
filehandler = open("wind_low_lcoe_summary_50_base.pickle","wb")
pickle.dump(wind_low_lcoe_summary_50_base, filehandler)
filehandler.close()
filehandler = open("wind_all_lcoe_summary_50_base.pickle","wb")
pickle.dump(wind_all_lcoe_summary_50_base, filehandler)
filehandler.close()
filehandler = open("solar_high_cf_summary_50_lc.pickle","wb")
pickle.dump(solar_high_cf_summary_50_lc, filehandler)
filehandler.close()
filehandler = open("solar_mid_cf_summary_50_lc.pickle","wb")
pickle.dump(solar_mid_cf_summary_50_lc, filehandler)
filehandler.close()
filehandler = open("solar_low_cf_summary_50_lc.pickle","wb")
pickle.dump(solar_low_cf_summary_50_lc, filehandler)
filehandler.close()
filehandler = open("solar_all_cf_summary_50_lc.pickle","wb")
pickle.dump(solar_all_cf_summary_50_lc, filehandler)
filehandler.close()
filehandler = open("solar_high_lcoe_summary_50_lc.pickle","wb")
pickle.dump(solar_high_lcoe_summary_50_lc, filehandler)
filehandler.close()
filehandler = open("solar_mid_lcoe_summary_50_lc.pickle","wb")
pickle.dump(solar_mid_lcoe_summary_50_lc, filehandler)
filehandler.close()
filehandler = open("solar_low_lcoe_summary_50_lc.pickle","wb")
pickle.dump(solar_low_lcoe_summary_50_lc, filehandler)
filehandler.close()
filehandler = open("solar_all_lcoe_summary_50_lc.pickle","wb")
pickle.dump(solar_all_lcoe_summary_50_lc, filehandler)
filehandler.close()
filehandler = open("wind_high_cf_summary_50_lc.pickle","wb")
pickle.dump(wind_high_cf_summary_50_lc, filehandler)
filehandler.close()
filehandler = open("wind_mid_cf_summary_50_lc.pickle","wb")
pickle.dump(wind_mid_cf_summary_50_lc, filehandler)
filehandler.close()
filehandler = open("wind_low_cf_summary_50_lc.pickle","wb")
pickle.dump(wind_low_cf_summary_50_lc, filehandler)
filehandler.close()
filehandler = open("wind_all_cf_summary_50_lc.pickle","wb")
pickle.dump(wind_all_cf_summary_50_lc, filehandler)
filehandler.close()
filehandler = open("wind_high_lcoe_summary_50_lc.pickle","wb")
pickle.dump(wind_high_lcoe_summary_50_lc, filehandler)
filehandler.close()
filehandler = open("wind_mid_lcoe_summary_50_lc.pickle","wb")
pickle.dump(wind_mid_lcoe_summary_50_lc, filehandler)
filehandler.close()
filehandler = open("wind_low_lcoe_summary_50_lc.pickle","wb")
pickle.dump(wind_low_lcoe_summary_50_lc, filehandler)
filehandler.close()
filehandler = open("wind_all_lcoe_summary_50_lc.pickle","wb")
pickle.dump(wind_all_lcoe_summary_50_lc, filehandler)
filehandler.close()